# MAFALDA code for "single-eyewall" periods
The following code applies the MAFALDA procedure to data from the "single-eyewall" time periods from all constant-SST axisymmetric simulations in CM1. The code then saves the outputs from this that we will use to make plots and derive trends with SST in various quantities, such as the mechanical efficiency.

In [ ]:
#Load modules
import datetime as dt
from numpy import dtype
import numpy as np
from pylab import *
import netCDF4 as n4
from netCDF4 import Dataset
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
from matplotlib import gridspec
import scipy.fftpack
from math import *
import xarray as xr
from scipy import integrate
from scipy import signal
from scipy.interpolate import RegularGridInterpolator
from scipy import spatial
from descartes import PolygonPatch
import shapely
from scipy.fft import fft, ifft
from shapely.geometry import Polygon
from shapely.geometry import LineString, Point
from PIL import Image
import os
import numpy.polynomial.polynomial as poly
from sklearn.metrics import r2_score
import numba
import matplotlib.ticker as ticker

In [ ]:
#Use this code to view available output variables from CM1
SST=295
ind=200
fileloc="/scratch/groups/oneillm/Laurel/SST_exps_3D/axisymm_exps/"+np.str(SST)+"/"+"cm1out_000"+np.str(ind)+".nc"
ds=xr.open_dataset(fileloc)
ds

## Define functions

The following function defines the MAFALDA analysis procedure that we apply to each "single-eyewall" period. 

The inputs to this code are:
1. The sea surface temperature for the current experiment
2. The timestep at the beginning of the single-eyewall period
3. The first timestep after the end of the single-eyewall period
4. The outer radius value, set to 600km for our study
5. The value of the constant, c, that is used to separate the eyewall and rainband circulations for their separate analyses. Specifically, if a trajectory derived from the isentropic streamfunction in this period experiences a maximum temperature differential that exceeds a value of c * (SST-T_tropopause), then all trajectories at the corresponding level of the isentropic streamfunction are denoted as belonging to the eyewall circulation. If this is not the case, they belong to the rainband circulation.

This function has no outputs, but saves several variables. The saved variables are as follows:
1. MAFALDA-derived energetic variables (for the full set of MAFALDA trajectories- or the "whole circulation" of the TC, for the eyewall circulation only, and for the rainband circulation only): the total heat input and output $Q_{in}$ and $Q_{out}$, the maximum available energy $W_{Max}$, the total useful energy $W=W_{P}+W_{KE}$, the water-lifting energy $W_{P}$, the total kinetic energy $W_{KE}$, the Gibbs penalty $\Delta G$, and the moisture penalty $W_{Moist}=W_{P}+\Delta G$.
2. MAFALDA-derived efficiency variables (for the full set of MAFALDA trajectories- or the "whole circulation" of the TC, for the eyewall circulation only, and for the rainband circulation only): the mechanical efficiency $\eta_{Mech}$, and the Carnot efficiency $\eta_{C}$.
3. MAFALDA-derived temperatures associated with the total heating and cooling of the TC, $T_{in}$ and $T_{out}$, for the full set of MAFALDA trajectories- or the "whole circulation" of the TC, for the eyewall circulation only, and for the rainband circulation only. 
4. Variables related to the MAFALDA-derived quantities (all calculated in the same subdomain that was used to calculate the MAFALDA-derived quantities): the kinetic energy per unit mass of dry air based on the maximum azimuthal wind speed at z=10m, the integrated kinetic energy of the TC's wind field at z=10m, the surface precipitation rate, and the total, latent, and sensible surface heat fluxes.
5. A quantity, "ov_flag", that tracks whether or not one or more level of the isentropic streamfunction was designated as corresponding to the eyewall circulation for the time period under consideration. If no eyewall circulation is identified, ov_flag has the value 1. If an eyewall circulation is identified, ov_flag has value 0. This variable is used by some of the code that is used to create plots and derive trends with SST from the outputs of this notebook, MAFALDA_plots.py.
6. Several variables that are used by Paper_plots.py and in another part of this notebook to make the figures in the main text and in the supplemental material

In [ ]:
def MAFALDA_process_singleeyewall(SST, tstart, tfinal, L_out, cval):
    #Define constants
    R = 287 #Gas constant for dry air (J/(K kg)). Matches the value in CM1
    Rv = 461.5 #Water vapor gas constant (J/(K kg)). Matches the value in CM1
    cpd = 1005.7 #Specific heat capacity of dry air in J/kg K. Matches the value in CM1
    cpv=1870 #Specific heat capacity of water vapor in J/kg K. Matches the value in CM1
    cpl = 4190 #Specific heat capacity of water at room temperature (J/ kg K). Matches the value in CM1 
    cpi=2106.0 #Specific heat of ice (J/kg K). Matches the value in CM1
    Lv0 = 2501000 #Latent heat of vaporization of water in J/kg. Matches the value in CM1
    kappa=R/cpd 
    T_f=273.15 #Freezing temperature (K)
    Ls=2834000.0 #Latent heat (J/kg) of sublimation at T=T_f=273.15K. Matches the value in CM1
    Lf0=Ls-Lv0#Latent heat of freezing (J/kg), Lf=Ls-Lv, at T=T0=273.15K (freezing temperature). 
    epsil=R/Rv
    grav=9.81 #Gravitational acceleration (m/s^2). Matches the value in CM1
    p_ref=100000 #Reference pressure in Pa. Matches the value in CM1
    T_ref=T_f #Reference temperature in K. Matches the value in CM1
    Lf=Lf0 #Assume that Lf is constant with respect to changes in temperature over the temperature range that we consider. This constant value is equal to Lf0.
    
    #Load data
    #Specify the location of the files- the code below accomodates the specific folder-naming system that I used for the simulations.
    if SST-floor(SST)==0: #Case where the SST is an integer
        root="/scratch/groups/oneillm/Laurel/SST_exps_3D/axisymm_exps/"+np.str(SST)+"/"
    elif SST-floor(SST)==0.5: #Case where the SST ends in ".5"
        root="/scratch/groups/oneillm/Laurel/SST_exps_3D/axisymm_exps/"+np.str(floor(SST))+"_5/"
    #Set the inner radius of the domain and optionally determine the radial index that corresponds to the input outer radius
    fileloc = root + 'cm1out_000001.nc' #Use the first data file from the simulation
    ds1=xr.open_dataset(fileloc)
    x_full=np.squeeze(ds1['xh']*1000).values #Full set of radial gridpoints in m
    L_inner=0 #Inner radius in km for the subdomain. Set to 0 to look at all radii up to the outer radius.
    L_o_ind=min(np.where(x_full>L_out*1000)[0]) #Index corresponding to the input outer radius
    z1=20 #Desired height in km up to which to load data
    z0=0 #Minimum height in km for loaded data
    L_outer=x_full[L_o_ind-1] #Outer radius. Same as input L_out, but in m.
    #print("Louter is "+np.str(L_outer))   
    #print("L_o_ind is "+np.str(L_o_ind))   
    
    #Load data from the axisymmetric CM1 simulations. The code assumes we saved the data in netcdf files
    x0 = L_inner; x1 = L_out; #Smallest and largest radii (km) for the loaded data. 
    for ind in np.arange(tstart, tfinal): #Step through data files, startung at the timestep specified by "tstart"
        if (ind < 1000)&(ind >= 100): 
            fileloc = root + 'cm1out_000'+np.str(ind)+'.nc'
        elif (ind < 100)&(ind >= 10): 
            fileloc = root + 'cm1out_0000'+np.str(ind)+'.nc'     
        elif ind<10:
            fileloc = root + 'cm1out_00000'+np.str(ind)+'.nc'        
        else:
            fileloc = root + 'cm1out_00'+np.str(ind)+'.nc'
        ds=xr.open_dataset(fileloc) #Open the netcdf file corresponding to the current timestep
        if ind==tstart: #Initialize all data arrays for the special case of ind=tstart
            temp_psfc=np.squeeze(ds['psfc'].sel(xh=slice(x0,x1))).values #Surface pressure (Pa)
            temp_psfc=temp_psfc[..., np.newaxis]
            psfc=temp_psfc
            temp_cd=np.squeeze(ds['cd'].sel(xh=slice(x0,x1))).values #Surface momentum exchange coefficient
            temp_cd=temp_cd[..., np.newaxis]
            cd=temp_cd 
            temp_ch=np.squeeze(ds['ch'].sel(xh=slice(x0,x1))).values #Surface sensible heat exchange coefficient. Same as surface exchange coefficient for moisture in our simulations
            temp_ch=temp_ch[..., np.newaxis]
            ch=temp_ch             
            temp_p=np.squeeze(ds['prs'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Pressure (Pa)
            temp_p=temp_p[..., np.newaxis]
            p=temp_p
            temp_th=np.squeeze(ds['th'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Potential temperature (K)
            temp_th=temp_th[..., np.newaxis]
            th=temp_th
            temp_qr=np.squeeze(ds['qr'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Rain water mixing ratio (kg/kg)
            temp_qr=temp_qr[..., np.newaxis]
            qr=temp_qr
            temp_qc=np.squeeze(ds['qc'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Cloud water mixing ratio (kg/kg)
            temp_qc=temp_qc[..., np.newaxis]
            qc=temp_qc
            temp_qi=np.squeeze(ds['qi'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Ice mixing ratio (kg/kg)
            temp_qi=temp_qi[..., np.newaxis]
            qi=temp_qi
            temp_qs=np.squeeze(ds['qs'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Snow mixing ratio (kg/kg)
            temp_qs=temp_qs[..., np.newaxis]
            qs=temp_qs
            temp_qg=np.squeeze(ds['qg'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Graupel mixing ratio (kg/kg)
            temp_qg=temp_qg[..., np.newaxis]
            qg=temp_qg
            temp_qv=np.squeeze(ds['qv'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Water vapor mixing ratio (kg/kg)
            temp_qv=temp_qv[..., np.newaxis]
            qv=temp_qv
            temp_w=np.squeeze(ds['winterp'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Vertical wind speed (m/s)
            temp_w=temp_w[..., np.newaxis]
            w=temp_w
            temp_v=np.squeeze(ds['vinterp'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Azimuthal wind speed (m/s)
            temp_v=temp_v[..., np.newaxis]
            v=temp_v
            temp_v10=np.squeeze(ds['v10'].sel(xh=slice(x0,x1))).values #Azimuthal wind speed at z=10m (m/s)
            temp_v10=temp_v10[..., np.newaxis]
            v10=temp_v10   
            temp_s10=np.squeeze(ds['s10'].sel(xh=slice(x0,x1))).values #Horizontal wind speed at z=10m (m/s)
            temp_s10=temp_s10[..., np.newaxis]
            s10=temp_s10 
            temp_u=np.squeeze(ds['uinterp'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Radial wind speed (m/s)
            temp_u=temp_u[..., np.newaxis]
            u=temp_u        
            temp_rho=np.squeeze(ds['rho'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values #Dry-air density (kg/m^3)
            temp_rho=temp_rho[..., np.newaxis]
            rho=temp_rho
            x=np.squeeze(ds['xh'].sel(xh=slice(x0,x1))*1000).values #Radial grid point values. Convert to m
            dx=np.mean(np.diff(x))  
            z=np.squeeze(ds['zh'].sel(zh=slice(z0,z1))*1000).values #Vertical grid points. Convert to m.             
            time=np.squeeze(ds['time'])
            temp_prate=np.squeeze(ds['prate'].sel(xh=slice(x0,x1))).values #Surface precipitation rate (kg/m^2/s)
            temp_prate=temp_prate[..., np.newaxis]
            prate=temp_prate
            temp_shflx=np.squeeze(ds['hfx'].sel(xh=slice(x0,x1))).values #Surface sensible heat flux (W/m^2)
            temp_shflx=temp_shflx[..., np.newaxis]
            shflx=temp_shflx
            temp_qvflx=np.squeeze(ds['qvflux'].sel(xh=slice(x0,x1))).values #Surface water vapor mixing ratio flux (g/g m/s) (same as kg/kg m/s)
            temp_qvflx=temp_qvflx[..., np.newaxis]
            qvflx=temp_qvflx            
            temp_qsfc=np.squeeze(ds['qsfc'].sel(xh=slice(x0,x1))).values #Surface water vapor mixing ratio (g/g) (same as kg/kg)
            temp_qsfc=temp_qsfc[..., np.newaxis]
            qsfc=temp_qsfc              
        #For the cases where the output variables have already been initialized, append data from the current timestamp to the existing arrays
        else:
            temp_rho=np.squeeze(ds['rho'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_rho=temp_rho[..., np.newaxis]
            rho=np.concatenate((rho, temp_rho), axis=2) 
        
            temp_w=np.squeeze(ds['winterp'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_w=temp_w[..., np.newaxis]
            w=np.concatenate((w, temp_w), axis=2) 
        
            temp_th=np.squeeze(ds['th'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_th=temp_th[..., np.newaxis]
            th=np.concatenate((th, temp_th), axis=2) 
        
            temp_qv=np.squeeze(ds['qv'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_qv=temp_qv[..., np.newaxis]
            qv=np.concatenate((qv, temp_qv), axis=2)
        
            temp_v=np.squeeze(ds['vinterp'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_v=temp_v[..., np.newaxis]
            v=np.concatenate((v, temp_v), axis=2)
            
            temp_u=np.squeeze(ds['uinterp'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_u=temp_u[..., np.newaxis]
            u=np.concatenate((u, temp_u), axis=2)        
            
            temp_v10=np.squeeze(ds['v10'].sel(xh=slice(x0,x1))).values
            temp_v10=temp_v10[..., np.newaxis]
            v10=np.concatenate((v10, temp_v10), axis=1)    
            
            temp_s10=np.squeeze(ds['s10'].sel(xh=slice(x0,x1))).values
            temp_s10=temp_s10[..., np.newaxis]
            s10=np.concatenate((s10, temp_s10), axis=1)              
        
            temp_qc=np.squeeze(ds['qc'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_qc=temp_qc[..., np.newaxis]
            qc=np.concatenate((qc, temp_qc), axis=2)
        
            temp_qi=np.squeeze(ds['qi'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_qi=temp_qi[..., np.newaxis]
            qi=np.concatenate((qi, temp_qi), axis=2)
        
            temp_qs=np.squeeze(ds['qs'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_qs=temp_qs[..., np.newaxis]
            qs=np.concatenate((qs, temp_qs), axis=2)
        
            temp_qg=np.squeeze(ds['qg'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_qg=temp_qg[..., np.newaxis]
            qg=np.concatenate((qg, temp_qg), axis=2)
        
            temp_qr=np.squeeze(ds['qr'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_qr=temp_qr[..., np.newaxis]
            qr=np.concatenate((qr, temp_qr), axis=2)
        
            time=np.squeeze(ds['time']) 
        
            temp_psfc=np.squeeze(ds['psfc'].sel(xh=slice(x0,x1))).values
            temp_psfc=temp_psfc[..., np.newaxis]
            psfc=np.append(psfc, temp_psfc, axis=1)
            
            temp_cd=np.squeeze(ds['cd'].sel(xh=slice(x0,x1))).values
            temp_cd=temp_cd[..., np.newaxis]
            cd=np.append(cd, temp_cd, axis=1)   
            
            temp_ch=np.squeeze(ds['ch'].sel(xh=slice(x0,x1))).values
            temp_ch=temp_ch[..., np.newaxis]
            ch=np.append(ch, temp_ch, axis=1)                  
        
            temp_p=np.squeeze(ds['prs'].sel(zh=slice(z0,z1),xh=slice(x0,x1))).values
            temp_p=temp_p[..., np.newaxis]
            p=np.concatenate((p, temp_p), axis=2) 
            
            temp_prate=np.squeeze(ds['prate'].sel(xh=slice(x0,x1))).values
            temp_prate=temp_prate[..., np.newaxis]
            prate=np.concatenate((prate, temp_prate), axis=1) 
            
            temp_shflx=np.squeeze(ds['hfx'].sel(xh=slice(x0,x1))).values
            temp_shflx=temp_shflx[..., np.newaxis]
            shflx=np.concatenate((shflx, temp_shflx), axis=1)     
            
            temp_qvflx=np.squeeze(ds['qvflux'].sel(xh=slice(x0,x1))).values
            temp_qvflx=temp_qvflx[..., np.newaxis]
            qvflx=np.concatenate((qvflx, temp_qvflx), axis=1)
            
            temp_qsfc=np.squeeze(ds['qsfc'].sel(xh=slice(x0,x1))).values
            temp_qsfc=temp_qsfc[..., np.newaxis]
            qsfc=np.concatenate((qsfc, temp_qsfc), axis=1)           
            
    ck_avg=np.mean(ch)
    cd_avg=np.mean(cd)

    #OPTIONAL: Plot the azimuthal wind field in z-r space for the chosen domain size
    r=x
    vmean=np.mean(v, axis=2) #Time-mean v field    
    [rplot, zplot]=np.meshgrid(r, z)
    plt.rc('axes', labelsize=40)    # fontsize of the x and y labels
    plt.rc('xtick', labelsize=30)    # fontsize of the x tick labels
    plt.rc('ytick', labelsize=30)    # fontsize of the x tick labels
    plt.rc('legend', fontsize=30)            # fontsize of the legend text    
    plt.figure(figsize=(15,10)) 
    plt.contourf(rplot/1000, zplot/1000, vmean, 20)
    plt.colorbar()
    plt.title("Azimuthal wind field", fontsize=30)
    plt.xlabel("Radius (km)")
    plt.ylabel("Height (km)")                         
            
    #Calculate various quantities: temperature, relative humidity, entropy, etc.
    t=th*(p/p_ref)**kappa #Temperature (K)
    Lv=Lv0+(cpv-cpl)*(t-T_ref) #Latent heat of vaporization of water (J/kg). Varies with temperature.
    es=Es(t) #Saturation vapor pressure (Pa) from Goff and Gratch (1946). 
    ep= p*Rv*qv/(R+Rv*qv) #Partial pressure of water vapor (Pa)
    pd=p-ep #Partial pressure of dry air (Pa)
    RH=ep/es #Relative Humidity
    #Calculate the moist entropy per unit mass of dry air (Pauluis 2016, JAS):
    qfr=qi+qg+qs #Mixing ratio of solid water (kg/kg)
    ql=qc+qr #Mixing ratio of liquid water (kg/kg)
    s_v=cpl*np.log(t/T_ref)+(Lv/t)-(Rv*np.log(RH)) #Specific entropy of water vapor (J/ kg K)
    s_dry= cpd*np.log(t/T_ref)-R*np.log(pd/p_ref) #Specific entropy of dry air (J/ kg K)
    s_l=cpl*np.log(t/T_ref) #Specific entropy of liquid water (J/ kg K)
    s_fr=cpi*np.log(t/T_ref)-Lf0/T_ref #Specific entropy of solid water (J/ kg K)
    entropy= s_dry+qv*s_v+ql*s_l+qfr*s_fr #Moist entropy per unit mass of dry air (J/ kg K)
    #OPTIONAL- divide moist entropy into the contributions from relative humidity (RH) and non-RH-dependent terms 
    entropy_RH=-qv*(Rv*np.log(RH)) #Portion of moist entropy due to RH
    entropy_nonRH=entropy-entropy_RH #Portion of moist entropy not due to RH
    #Find equivalent potential temperature. Matches the formulation in CM1.
    ee=0.01*p*qv/(epsil+qv) #Same as ep but in hPa. Matches CM1 formulation.
    tlcl=55.0+2840.0/(3.5*np.log(t)-np.log(1.0e-20+ee)-4.805) #Temperature at the LCL. Matches CM1 formulation.  
    th_e=t*((p_ref/p)**(0.2854*(1.0-0.28*qv)))*np.exp(((3376.0/tlcl)-2.54)*qv*(1.0+0.81*qv)) #Equivalent potential temperature. Matches CM1 formulation
    alpha_d=(R*t+Rv*qv*t)/p #Specific volume per unit mass of dry air (m^3/kg) (Pauluis 2016, JAS).
    #Find specific gibbs free energies
    gv=cpl*(t-T_ref-t*np.log(t/T_ref))+Rv*t*np.log(RH) #Specific gibbs free energy of water vapor (J/kg) (Pauluis, 2016, JAS).
    gl=cpl*(t-T_ref-t*np.log(t/T_ref)) #Specific gibbs free energy of liquid water (J/kg) (Pauluis, 2016, JAS).
    gi=cpi*(t-T_ref-t*np.log(t/T_ref))-Lf0*(1-t/T_ref) #Specific gibbs free energy of solid water (J/kg) (Pauluis, 2016, JAS).
    WP_integrand=grav*(qv+ql+qfr) #Use to find the water-lifting term, Wp. See Pauluis and Zhang (2017, JAS) equation (6).
    #OPTIONAL- Calculate of moist enthalpy per unit mass of dry air
    hd=cpd*(t-T_f)
    hv=cpl*(t-T_f)+Lv
    hl=cpl*(t-T_f)
    hi=cpi*(t-T_f)-Lf0
    h=hd+qv*hv+ql*hl+qfr*hi    

    #OPTIONAL- Find anomalous (with respect to horizontal average) and horizontal-average alpha_d and p.
    perArea=np.sum(x) #Equivalent to "horizontal area" of subdomain. We don't include a factor of "dx" or multiply by 2*pi because the fact that these 
                    #values are constant for our simulations means they cancel out with the numerator integrals that we divide by "perArea"
    xlen=x.size
    zlen=z.size
    x=x.reshape(1, xlen, 1) #Change the shape of x for the following calculation
    a_d_av= np.sum(alpha_d*x, axis=1)/perArea #Horizontal mean of alpha_d. This has the wrong dimensions for what we want to do next, so in what follows we will pad it such that it has the same dimensions as alpha_d.
    p_av= np.sum(p*x, axis=1)/perArea #Horizontal mean of pressure.
    a_d_avg=np.zeros((zlen, xlen, (tfinal-tstart)))  #Initialize a_d_avg, which will serve as the "padded" version of a_d_av, with the same dimensions as alpha_d
    p_avg=np.zeros((zlen, xlen, (tfinal-tstart)))
    for xind in np.arange(0, xlen):
        a_d_avg[:, int(xind), :]=a_d_av #For each radius, set a column of a_d_avg to be equal to a_d_av. This ensures a_d_avg is equivalent to a_d_av but with the same dimensions as alpha_d
        p_avg[:, int(xind), :]=p_av
    panom=p-p_avg #Anomalous pressure with respect to horizontal average
    a_danom=alpha_d-a_d_avg #Anomalous specific volume with respect to horizontal average
    x=x.reshape(xlen) #Change the shape of x back to what it was before

    #Find the anomalous (with respect to the horizontal average) vertical mass flux, rho*w.
    f=rho*w #Vertical mass flux
    #Remove horizontal-mean vertical mass flux from the vertical mass flux to get the anomalous vertical mass flux
    perArea=np.sum(x) 
    xlen=x.size
    zlen=z.size
    x=x.reshape(1, xlen, 1) #Change the shape of x for the following calculation
    f_av= np.sum(f*x, axis=1)/perArea #Horizontal mean of the vertical mass flux. This has the wrong dimensions for what we want to do next, so in what follows we will pad it such that it has the same dimensions as f.
    f_avg=np.zeros((zlen, xlen, (tfinal-tstart)))  #Initialize f_avg, which will serve as the "padded" version of f_av, with the same dimensions as f
    for xind in np.arange(0, xlen):
        f_avg[:, int(xind), :]=f_av #For each radius, set a column of f_avg to be equal to f_av. This ensures f_avg is equivalent to f_av but with the same dimensions as f
    f=f-f_avg #Remove horizontal-mean vertical mass flux from f to get the anomalous vertical mass flux
    x=x.reshape(xlen) #Change the shape of x back to what it was before

     #OPTIONAL- Separate the positive and negative vertical mass flux from each other
    [zlen, rlen, tlen]=shape(f)
    f_neg=np.zeros((zlen, rlen, tlen))
    f_pos=np.zeros((zlen, rlen, tlen))
    for i in np.arange(zlen):
        for j in np.arange(rlen):
            for k in np.arange(tlen):
                if f[i, j, k]<0:
                    f_neg[i, j, k]=f[i, j, k] #Negative vertical mass flux
                elif f[i, j, k]>0:
                    f_pos[i, j, k]=f[i, j, k] #Positive vertical mass flux                   

    #Perform the isentropic integral of the vertical mass flux, based on a modified verion of Mrowiec et al. (2016, JAS) equation (2).
    #We approximate the theta_e delta function in this formula by binning the mass flux at all according to the value of 
    #the equivalent potential temperature theta_e.

    #Set parameters of the theta_e bins.
    delt=0.5 #Half-width of theta_e bins
    th_min=295 #Minimum value of theta_e for the bins
    th_max=450 #Maximum value of theta_e for the bins
    
    number=(th_max-th_min)/(2*delt) #Number of theta_e bins
    bins=np.arange(th_min-delt, th_max+delt, delt*2) #Define theta_e bins based on the parameters th_min, th_max, and delt

    #Perform the isentropic integral to get <rho*w>(z, theta_e, t), and store in f2. We then divide by perArea to get the isentropic-average vertical mass flux
    #The following code loops through theta_e bins defined above and searches for the points (r, z, t) with theta_e values that fall inside these bins
    #Once these points (r, z, t) are obtained, the code performs the isentropic horizontal integral for each z value. The result of this is stored in f2b.
    #After this, the vector f2b (which has dimensions zx1xt) is added to the array f2 as a column. f2 has dimensions of zx(number of theta_e bins)xt
    for b in bins: #"For a given theta e bin, do the following"
        if b != bins[int(number)]: #Don't deal with last bin since it is redundant given how I write the next line- would be like counting the last bin twice
            #print("Doing this")
            [zindex, xindex, tindex]=np.where((th_e>b) & (th_e<=b+1)) #Get indices of all points (r, z, t) at which theta_e values fall within the theta_e bin of interest. 
            #In what follows, a single such point (r, z, t) would be given by (x[xindex[i]], z[zindex[i]], t[tindex[i]]), where i is some index between 0 and the length of xindex.
            f2b=np.zeros((zlen, 1, (tfinal-tstart))) #Initialize f2b, which will hold the result of the isentropic integral for given values of z, t, and a given theta e bin. Dimensions are zx1xt
            #Now that we have found the points (r, z, t) of interest for a given theta_e bin, we calculate the isentropic integral wrt r for each z value
            for i in np.unique(zindex): #"Do the following for a given z value in the set of points denoted by zindex, xindex, and tindex"
                for m in np.unique(tindex[zindex==i]): #"Within the subset of t values corresponding to the current z value, do the following"
                    integrand=[] 
                    indices=np.where((zindex==i)&(tindex==m))[0] #For the chosen z and t values, z' and t', find all points (r, z=z', t=t')
                    #For the chosen z and t values, z' and t', calculate the integrand at all points (r, z=z', t=t'): (rho*w)'(r, z=z', t=t')*r 
                    for j in indices:
                        integrand.append(f[i, xindex[j], m]*x[xindex[j]]) #Calculate the integrand, (rho*w)'(r, z=z', t=t')*r , at all points (r, z=z', t=t')  
                    f2b[i, :, m]=np.sum(integrand, axis=0) #Perform the isentropic integral: <rho*w>(theta_e bin, z=z', t=t')=integral((rho*w)'(r, z=z', t=t')*r dr, limits: (0, L_outer))
            #f2b contains the result of the isentropic integral for all values of t and z corresponding to the current theta_e bin.
            #Now, we add f2b to f2 in the position corresponding to the current theta_e bin.
            if b==bins[0]: #For the first bin, we need to handle things as a special case to initialize f2
                    f2=f2b #Initialize f2, which contains the result of the isentropic integral at all values of z, t, and theta_e
            else: 
                f2=np.concatenate((f2, f2b), axis=1) #Concatenate f2b along the theta_e dimension of f2
    f2=f2/perArea #Divide f2 by the horizontal area of the domain to obtain the isentropic-average vertical mass flux, <rho*w>(z, theta_e, t)           

    #Time integral of f2. 
    f_tavg=np.sum(f2, axis=2) #Integrate along the time axis. No need to multiply by dt because if we divide by tfinal-tstart (time period in units of # of timestamps) then dt=1 timestamp
    f_tavg=f_tavg/(tfinal-tstart) #Divide by tau=tfinal-tstart   
    
    #Find the isentropic streamfunction using the non-time-averaged isentropic-average vertical mass flux, following a modified version of equation (4) of Mrowiec et al. (2016, JAS)
    [zlen, thelen]=shape(f_tavg)
    thevec=arange(thelen) #Indices in theta_e dimension   
    for i in thevec:
        if i==0:
            f3=f2[:, i, :]*2*delt #Perform integral, psi(z, theta_e)=integral(<rho*w>(z, theta_e', t) dtheta_e', limits: (0, theta_e)), for the first theta_e value
            f3=f3[..., np.newaxis] #Gives f3 the correct shape, so we can append it to psi_t
            psi_t=f3 #Add the result of the integral to psi_t
        else:
            f3=np.sum((f2[:, 0:i, :]*2*delt), axis=1) #Perform integral, psi(z, theta_e, t)=integral(<rho*w>(z, theta_e', t) dtheta_e', limits: (0, theta_e)), for a given theta_e value
            f3=f3[..., np.newaxis] #Gives f3 the correct shape, so we can append it to psi_t
            psi_t=np.concatenate((psi_t, f3), axis=2) #Add the result of the integral to psi_t 
    psi=np.sum(psi_t, axis=1) #Find time-average isentropic streamfunction. As before, no need to multiply by dt because if we divide by tfinal-tstart (time period in units of # of timestampe) then dt=1 timestamp
    psi=psi/(tfinal-tstart) #Divide by tau=tfinal-tstart 

    #Plot isentropic streamfunction. 
    plt.rc('axes', labelsize=40)    # fontsize of the x and y labels
    plt.rc('xtick', labelsize=40)    # fontsize of the x tick labels
    plt.rc('ytick', labelsize=40)    # fontsize of the x tick labels
    plt.rc('legend', fontsize=40)            # fontsize of the legend text    
    plt.figure(figsize=(15,10)) 
    theta_es=np.arange(th_min, th_max, delt*2)
    [zplot, thplot]=np.meshgrid(theta_es, z) 
    ncontour = 25
    contourarray = psi.min()*((2*np.arange((ncontour+1),1.0, -1.0)-1)/(2*ncontour))
    plt.contour(zplot, thplot/1000, psi,contourarray, cmap='viridis') #Set to 25 contours not 30 bc this is what we use later!
    cbar=plt.colorbar(format=ticker.FuncFormatter(fmt))
    plt.title('Isentropic Streamfunction (kg $m^{-2}$ $s^{-1}$)', fontsize=40)
    plt.ylabel('Height (km)')
    plt.xlabel('Equivalent Potential Temperature (K)')
    plt.rc('axes', labelsize=40)    # fontsize of the x and y labels
    plt.rc('xtick', labelsize=40)    # fontsize of the x tick labels
    plt.rc('ytick', labelsize=40)    # fontsize of the x tick labels
    plt.rc('legend', fontsize=40)            # fontsize of the legend text
    xlim(th_min, th_max)   
    ylim(-1, np.max(z)/1000)

    #Get the coordinates of all levels of the isentropic streamfunction from a contour plot of it. 
    #We will use the closed loops at each level of the streamfunction to construct "MAFALDA trajectories".
    #These trajectories are assumed to represent the mean trajectories of real air parcels in the TC in z-theta_e space.
    plt.figure() #Make a new figure so we don't overplot on the previous one
    ncontour = 25 #Number of levels to use in our contour plot of the isentropic streamfunction
    contourarray = psi.min()*((2*np.arange((ncontour+1),1.0, -1.0)-1)/(2*ncontour)) #Sets the levels of the isentropic streamfunction that we will plot as contours
    h1 = plt.contour(zplot,thplot,psi,contourarray,cmap='rainbow') #Contour plot of the isentropic streamfunction
    contcoords = h1.allsegs #Coordinates of MAFALDA trajectories corresponding to each level of the isentropic streamfunction
    contlevels=h1.levels #Values of all levels of the isentropic streamfunction

    #Find mass-weighted isentropic- and time-average (denoted "mass-weighted isentropic-average" for simplicity below) 
    #variables: temperature, moist entropy, etc. See Pauluis (2016, JAS) equation (4)
    #Note that the user does not need to perform the mass-weighting here if the input data is model output with pressure rather than height as the vertical coordinate.
    x2=x.reshape(1, xlen, 1)
    perArea2=np.sum(np.sum(rho*x2, axis=1), axis=1) #Horizontal-average of dry-air density
    rhot_avg=isentropic_integral(rho*t, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Isentropic-average of dry air density * temperature
    rho_avg=isentropic_integral(rho, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Isentropic-average dry-air density
    #Convert zeros, which occur because of how we have encoded the isentropic averaging process, in "rho_avg" to nan values for simplicity. 
    rho_avg_nan=rho_avg
    rho_avg_nan[rho_avg_nan==0]=nan
    rhot_avg_nan=rhot_avg
    rhot_avg_nan[rhot_avg_nan==0]=nan
    t_IA=rhot_avg_nan/rho_avg_nan #Mass-weighted isentropic-average temperature
    #Repeat the above procedure for moist entropy, pressure, etc.
    rhoent_avg=isentropic_integral(rho*entropy, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Isentropic-average rho * (moist entropy)
    rhoent_avg_nan=rhoent_avg
    rhoent_avg_nan[rhoent_avg_nan==0]=nan
    entropy_IA=rhoent_avg_nan/rho_avg_nan #Mass-weighted isentropic-average moist entropy per unit mass of dry air
    rhop_avg=isentropic_integral(rho*p, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) 
    rhop_avg_nan=rhop_avg
    rhop_avg_nan[rhop_avg_nan==0]=nan
    p_IA=rhop_avg_nan/rho_avg_nan #Mass-weighted isentropic-average pressure
    rhoad_avg=isentropic_integral(rho*alpha_d, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) 
    rhoad_avg_nan=rhoad_avg
    rhoad_avg_nan[rhoad_avg_nan==0]=nan
    ad_IA=rhoad_avg_nan/rho_avg_nan #Mass-weighted isentropic-average specific volume per unit mass of dry air
    rhogv_avg=isentropic_integral(rho*gv, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) 
    rhogv_avg_nan=rhogv_avg
    rhogv_avg_nan[rhogv_avg_nan==0]=nan
    gv_IA=rhogv_avg_nan/rho_avg_nan #Mass-weighted isentropic-average gibbs free energy of water vapor
    rhogl_avg=isentropic_integral(rho*gl, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) 
    rhogl_avg_nan=rhogl_avg
    rhogl_avg_nan[rhogl_avg_nan==0]=nan
    gl_IA=rhogl_avg_nan/rho_avg_nan #Mass-weighted isentropic-average gibbs free energy of liquid water
    rhogi_avg=isentropic_integral(rho*gi, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal)
    rhogi_avg_nan=rhogi_avg
    rhogi_avg_nan[rhogi_avg_nan==0]=nan
    gi_IA=rhogi_avg_nan/rho_avg_nan #Mass-weighted isentropic-average gibbs free energy of solid water
    rhoqv_avg=isentropic_integral(rho*qv, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal)
    rhoqv_avg_nan=rhoqv_avg
    rhoqv_avg_nan[rhoqv_avg_nan==0]=nan    
    qv_IA=rhoqv_avg_nan/rho_avg_nan #Mass-weighted isentropic-average water vapor mixing ratio
    rhoql_avg=isentropic_integral(rho*ql, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal)
    rhoql_avg_nan=rhoql_avg
    rhoql_avg_nan[rhoql_avg_nan==0]=nan
    ql_IA=rhoql_avg_nan/rho_avg_nan #Mass-weighted isentropic-average liquid water mixing ratio
    rhoqi_avg=isentropic_integral(rho*qfr, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal)
    rhoqi_avg_nan=rhoqi_avg
    rhoqi_avg_nan[rhoqi_avg_nan==0]=nan
    qi_IA=rhoqi_avg_nan/rho_avg_nan  #Mass-weighted isentropic-average solid water mixing ratio
    rhoWPint_avg=isentropic_integral(rho*WP_integrand, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal)
    rhoWPint_avg_nan=rhoWPint_avg
    rhoWPint_avg_nan[rhoWPint_avg_nan==0]=nan
    WPint_IA=rhoWPint_avg_nan/rho_avg_nan #Mass-weighted isentropic-average of "WP_integrand"
    #OPTIONAL- compute isentropic-average mass-weighted entropy contributions due to RH and not due to RH.
    rhoent_RH_avg=isentropic_integral(rho*entropy_RH, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal)
    rhoent_RH_avg_nan=rhoent_RH_avg
    rhoent_RH_avg_nan[rhoent_RH_avg_nan==0]=nan
    entropy_RH_IA=rhoent_RH_avg_nan/rho_avg_nan
    rhoent_nRH_avg=isentropic_integral(rho*entropy_nonRH, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal)
    rhoent_nRH_avg_nan=rhoent_nRH_avg
    rhoent_nRH_avg_nan[rhoent_nRH_avg_nan==0]=nan
    entropy_nRH_IA=rhoent_nRH_avg_nan/rho_avg_nan  
    #OPTIONAL- compute isentropic-average mass-weighted average and anomalous pressure and specific volume per unit mass of dry air
    rhopa_avg=isentropic_integral(rho*panom, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Pressure anomaly in domain
    rhopa_avg_nan=rhopa_avg
    rhopa_avg_nan[rhopa_avg_nan==0]=nan
    panom_IA=rhopa_avg_nan/rho_avg_nan
    rhoadav_avg=isentropic_integral(rho*a_d_avg, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Average alpha_d in domain
    rhoadav_avg_nan=rhoadav_avg
    rhoadav_avg_nan[rhoadav_avg_nan==0]=nan
    adav_IA=rhoadav_avg_nan/rho_avg_nan   
    rhopav_avg=isentropic_integral(rho*p_avg, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Pressure anomaly in domain
    rhopav_avg_nan=rhopav_avg
    rhopav_avg_nan[rhopav_avg_nan==0]=nan
    pav_IA=rhopav_avg_nan/rho_avg_nan
    rhoada_avg=isentropic_integral(rho*a_danom, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Average alpha_d in domain
    rhoada_avg_nan=rhoada_avg
    rhoada_avg_nan[rhoada_avg_nan==0]=nan
    adanom_IA=rhoada_avg_nan/rho_avg_nan  
    #OPTIONAL- compute isentropic-average mass-weighted relative humidity
    rhoRH_avg=isentropic_integral(rho*RH, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Average alpha_d in domain
    rhoRH_avg_nan=rhoRH_avg
    rhoRH_avg_nan[rhoRH_avg_nan==0]=nan
    RH_IA=rhoRH_avg_nan/rho_avg_nan  
    #OPTIONAL- compute isentropic-average mass-weighted moist enthalpy per unit mass of dry air
    rhoh_avg=isentropic_integral(rho*h, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Average alpha_d in domain
    rhoh_avg_nan=rhoh_avg
    rhoh_avg_nan[rhoh_avg_nan==0]=nan
    h_IA=rhoh_avg_nan/rho_avg_nan     
    #OPTIONAL- compute isentropic-average positive and negative vertical mass fluxes. 
    f_neg_IA=isentropic_integral(f_neg, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Negative vertical mass flux 
    f_pos_IA=isentropic_integral(f_pos, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal) #Positive vertical mass flux 
    
    #Interpolate the mass-weighted isentropic- and time-averaged variables onto the gridpoints of the MAFALDA trajectories.
    #Initialize interpolator functions
    interpolator_temp = RegularGridInterpolator((z,theta_es),t_IA) 
    interpolator_entropy = RegularGridInterpolator((z,theta_es),entropy_IA)
    interpolator_p = RegularGridInterpolator((z,theta_es),p_IA)
    interpolator_ad = RegularGridInterpolator((z,theta_es),ad_IA)  
    interpolator_gv = RegularGridInterpolator((z,theta_es),gv_IA)  
    interpolator_gl = RegularGridInterpolator((z,theta_es),gl_IA) 
    interpolator_gi = RegularGridInterpolator((z,theta_es),gi_IA)      
    interpolator_qv = RegularGridInterpolator((z,theta_es),qv_IA)  
    interpolator_ql = RegularGridInterpolator((z,theta_es),ql_IA) 
    interpolator_qi = RegularGridInterpolator((z,theta_es),qi_IA) 
    interpolator_WPint = RegularGridInterpolator((z,theta_es),WPint_IA) 
    #OPTIONAL- initialize interpolator functions for the optionally-calculated quantities from above.
    interpolator_entropy_RH = RegularGridInterpolator((z,theta_es),entropy_RH_IA)
    interpolator_entropy_nRH = RegularGridInterpolator((z,theta_es),entropy_nRH_IA)    
    interpolator_pa = RegularGridInterpolator((z,theta_es),panom_IA)
    interpolator_adav = RegularGridInterpolator((z,theta_es),adav_IA) 
    interpolator_pav = RegularGridInterpolator((z,theta_es),pav_IA)
    interpolator_ada = RegularGridInterpolator((z,theta_es),adanom_IA)  
    interpolator_RH = RegularGridInterpolator((z,theta_es),RH_IA)
    interpolator_h = RegularGridInterpolator((z,theta_es),h_IA)
    #Get the theta_e and z values of each MAFALDA trajectory as two separate lists- one for theta_e values and one for z values
    interpolant_th=[]
    interpolant_z=[]
    levels=[]
    #Assign maximum theta_e and z values for each SST, where a MAFALDA trajectory that exceeds these values is ignored by the code.
    #This code is included because the isentropic-averaging procedure sometimes (rarely) produces "contrail" artefacts- mostly-horizontal lines
    #in z-theta_e space that extend upwards in theta_e from the isentropic streamfunction. These "contrails" are artefacts of the code 
    #and are not physical, so we ignore them in our analysis.
    #These maximum values are set by inspection of the isentropic streamfunctions.
    if SST==295:
        maxt=345
        maxz=14000
    elif SST==295.5:
        maxt=350
        maxz=14000
    elif SST==296:
        maxt=350
        maxz=14000
    elif SST==296.5:
        maxt=355
        maxz=14500
    elif SST==297:
        maxt=355
        maxz=14500
    elif SST==297.5:    
        maxt=355
        maxz=14500
    elif SST==298:
        maxt=360
        maxz=14500
    elif SST==298.5:
        maxt=365
        maxz=15000
    elif SST==299:
        maxt=365
        maxz=15000
    elif SST==299.5:
        maxt=370
        maxz=15000
    elif SST==300:
        maxt=370
        maxz=15000
    elif SST==300.5:
        maxt=375
        maxz=15000
    elif SST==301:
        maxt=380
        maxz=16000
    elif SST==301.5:
        maxt=380
        maxz=16000
    elif SST==302:
        maxt=380
        maxz=16000
    elif SST==302.5:
        maxt=380
        maxz=16000
    elif SST==303:
        maxt=400
        maxz=17000
    elif SST==303.5:
        maxt=400
        maxz=17000
    elif SST==304:
        maxt=400
        maxz=17000
    elif SST==304.5:
        maxt=400
        maxz=17000
    elif SST==305:
        maxt=400
        maxz=17000
    elif SST==305.5:
        maxt=400
        maxz=17000        
    elif SST==306:
        maxt=410
        maxz=17000
    elif SST==306.5:
        maxt=410
        maxz=18000
    elif SST==307:
        maxt=410
        maxz=18000        
    elif SST==307.5:
        maxt=420
        maxz=18000   
    for cont in np.arange(0, len(contcoords)): #Loop through the levels of the isentropic streamfunction. 
        clevel=contlevels[cont]
        if contcoords[cont]: #Only do the following if the list for the chosen contour is not empty
            for j in np.arange(0, len(contcoords[cont])): #Loop through all MAFALDA trajectories at this level of the isentropic streamfunction. There may be more than one of these.
                ccont=contcoords[cont][j]
                if (max(ccont[:, 0])<maxt)&(max(ccont[:, 1]<maxz)): #Don't count "contrails"
                    interpolant_th_ar=ccont[:, 0] #Theta_e points on the trajectory
                    interpolant_z_ar=ccont[:, 1] #z points on the trajectory
                    interpolant_th_l=interpolant_th_ar.tolist() 
                    interpolant_z_l=interpolant_z_ar.tolist()
                    if (interpolant_th_l[0]!=interpolant_th_l[-1]): #To construct a trajectory that is truly a "closed loop", we must add the first point in the trajectory as its last point.
                        interpolant_th_l.append(interpolant_th_l[0])
                        interpolant_z_l.append(interpolant_z_l[0])
                    interpolant_th_a=np.asarray(interpolant_th_l)
                    interpolant_z_a=np.asarray(interpolant_z_l)
                    levels.append(clevel) #Record the value of the isentropic streamfunction level corresponding to each MAFALDA trajectory
                    interpolant_th.append(interpolant_th_a) #Contains the sets of theta_e points for all MAFALDA trajectories
                    interpolant_z.append(interpolant_z_a) #Contains the sets of z points for all MAFALDA trajectories
    interpolant_th_arr=np.asarray(interpolant_th) #Convert to a numpy array
    interpolant_z_arr=np.asarray(interpolant_z)


    #Make interpolant_th_arr and interpolant_z_arr into an input to the interpolator functions, 
    #which must be a set of points of the form [[zcoord, thcoord], [zcoord, thcoord], ...]
    endi=len(interpolant_th_arr)
    for i in np.arange(0, endi):
        endj=len(interpolant_th_arr[i])
        if i==0:
            for j in np.arange(0, endj):
                if j==0:
                    interpolant_list_cont=[[interpolant_z_arr[i][j], interpolant_th_arr[i][j]]]
                else:
                    interpolant_list_cont.append([interpolant_z_arr[i][j], interpolant_th_arr[i][j]])
            interpolant_arr_cont=np.asarray(interpolant_list_cont)
            interpolant_list=[interpolant_arr_cont]
        else:
            for j in np.arange(0, endj):
                if j==0:
                    interpolant_list_cont=[[interpolant_z_arr[i][j], interpolant_th_arr[i][j]]]
                else:
                    interpolant_list_cont.append([interpolant_z_arr[i][j], interpolant_th_arr[i][j]])
            interpolant_arr_cont=np.asarray(interpolant_list_cont)
            interpolant_list.append(interpolant_arr_cont)
    interpolant_array=np.asarray(interpolant_list) #Contains the set of points, for all MAFALDA trajectories, formatted
                                                   #as a set of points of the form [[zcoord, thcoord], [zcoord, thcoord], ...]

    #The above produced a set of points [z, th] that the trajectories trace through in "time". Here, we get the values of variables, including temperature and entropy, at each point going forward in "time"
    #along each MAFALDA trajectory. We then convert the values of these variables at each point along a given MAFALDA trajectory to a "timeseries" of the variable as we go along the MAFALDA trajectory.
    #Note that this "time" does not correspond to the real time elapsed for a path travelled by any physical parcel. It is rather the "time" taken for an imaginary mean parcel to circulate around the MAFALDA trajectory.
    #Initialize all "timeseries"
    interpolated_t=[]
    interpolated_ent=[]
    interpolated_ad=[]
    interpolated_p=[]
    interpolated_gv=[]
    interpolated_gl=[]
    interpolated_gi=[]
    interpolated_qv=[]
    interpolated_ql=[]
    interpolated_qi=[] 
    interpolated_WPint=[] 
    #OPTIONAL- initialize "timeseries" of optionally- calculated variables
    interpolated_ent_RH=[]
    interpolated_ent_nRH=[]    
    interpolated_panom=[] 
    interpolated_adav=[] 
    interpolated_pav=[] 
    interpolated_adanom=[] 
    interpolated_RH=[]
    interpolated_h=[]
    
    levels2=[]

    #Interpolate to find the "timeseries" of all variables along each MAFALDA trajectory
    for i in np.arange(endi):
        #print(i)
        if size(np.where(interpolant_array[i]<25.0001)[0])>0: #If the MAFALDA trajectory contains z-value(s) exactly equal to 25, the lowest value of z that we input to the interpolator functions above,
                                                              #this breaks the interpolator function. To deal with this, if z=25 for any trajectory, we increase this z-value by 0.01. 
            listz=np.where(interpolant_array[i]<25.0001)[0] #Find the indices of the points where z=25
            for ind in listz:
                interpolant_array[i][ind, 0]+=0.001 #This barely changes the value while putting it within the bounds of the interpolator functions' capabilities              
        #Interpolate!
        interpolated_t.append(interpolator_temp(interpolant_array[i]))
        interpolated_ent.append(interpolator_entropy(interpolant_array[i]))
        interpolated_p.append(interpolator_p(interpolant_array[i]))
        interpolated_ad.append(interpolator_ad(interpolant_array[i]))  
        interpolated_gv.append(interpolator_gv(interpolant_array[i])) 
        interpolated_gl.append(interpolator_gl(interpolant_array[i])) 
        interpolated_gi.append(interpolator_gi(interpolant_array[i])) 
        interpolated_qv.append(interpolator_qv(interpolant_array[i])) 
        interpolated_ql.append(interpolator_ql(interpolant_array[i])) 
        interpolated_qi.append(interpolator_qi(interpolant_array[i]))
        interpolated_WPint.append(interpolator_WPint(interpolant_array[i])) 
        #OPTIONAL- interpolate for the optionally-calculated variables
        interpolated_ent_RH.append(interpolator_entropy_RH(interpolant_array[i]))
        interpolated_ent_nRH.append(interpolator_entropy_nRH(interpolant_array[i]))        
        interpolated_panom.append(interpolator_pa(interpolant_array[i]))
        interpolated_adav.append(interpolator_adav(interpolant_array[i]))  
        interpolated_pav.append(interpolator_pav(interpolant_array[i]))
        interpolated_adanom.append(interpolator_ada(interpolant_array[i])) 
        interpolated_RH.append(interpolator_RH(interpolant_array[i])) 
        interpolated_h.append(interpolator_h(interpolant_array[i])) 
    
        levels2.append(levels[i]) #Current level for the MAFALDA trajectory we are interpolating       

    #Select which MAFALDA trajectories belong to the eyewall and rainband circulations.
    #This is based on whether the maximum temperature difference across a trajectory, determined using interpolated_t,
    #exceeds some fraction, c=0.8, of SST-T_tropopause. If it does then all trajectories at this level of the isentropic
    #streamfunction are eyewall circulation trajectories. If no trajectory at a given level satisfies this condition then 
    #all trajectories at that level belong to the rainband circulation.
    endc=len(interpolated_ent)
    interpolated_t_nan=interpolated_t
    for cnum in np.arange(0,endc):
        if isinstance(interpolated_t[cnum], np.ndarray): #For MAFALDA trajectories that are not single points, set all nan values to 0.
                                                         #If this is not done then the max and/or min of the trajectories will return "nan" values
            interpolated_t_nan[cnum][np.isnan(interpolated_t_nan[cnum])] = 0
    Tmax_deep=SST 
    Tmin_deep=np.load('tropopause_'+np.str(SST)+'.npz')['t_trop'] 
    delT_deep=Tmax_deep-Tmin_deep #SST-T_tropopause
    overturning_threshold=cval #Fraction of (SST-T_tropopause) that will result in an "eyewall circulation" designation. 
    overturning_cnums=[] #Contains the trajectory numbers corresponding to the eyewall circulation
    overturning_levels=[] #Contains the levels corresponding to the eyewall circulation
    rainband_levels=[] #Contains the levels corresponding to the rainband circulation
    rainband_cnums=[] #Contains the trajectory numbers corresponding to the rainband circulation
    for cnum in np.arange(0,endc): #Loop through all MAFALDA trajectories
        Tmax=np.max(interpolated_t_nan[cnum]) #Maximum temperature value achieved by the current trajectory
        nonzero_inds=np.where(interpolated_t_nan[cnum]>0)[0]  
        Tmin=Tmax #Initial "guess" for the minimum temperature
        #We have replaced all "nan" values in interpolated_t with zero-values. If we try to find a minimum in interpolated_t[cnum]
        #without accounting for this, then the code will just return zero as the minimum. 
        #In order to account for this, in what follows we find the minimum temperature for the trajectory using only values of
        #interpolated_t[cnum] that are greater than zero.
        for ind in nonzero_inds: #Look only at values in interpolated_t[cnum] that are greater than zero.
            Tmin_new=interpolated_t[cnum][ind]
            if Tmin_new<Tmin: #If the current temperature value from interpolated_t[cnum] is less than the current "guess" at Tmin, update the "guess"
                Tmin=Tmin_new #Update the "guess" for the minimum temperature value achieved by the current trajectory
        delT=Tmax-Tmin #Maximum temperature difference across the current trajectory
        #If a trajectory at a certain level belongs to eyewall circulation, add all other (typically very small) trajectories at that level to the eyewall circulation.
        #This avoids "messing up" future calculations for the rainband circulation by weighting the behavior of small circulations at these levels equally to the 
        #(usually larger) "main" circulations at other rainband levels
        if delT>overturning_threshold*delT_deep: 
            overturning_levels.append(levels2[cnum]) #Add the level corresponding to the current trajectory as an "eyewall circulation level"
        elif delT<0: #This should not be possible given how the code is written
            print("ERROR!!!- delT<0")
    #Assign all trajectories at "eyewall circulation levels" to the eyewall circulation. Assign the rest to the rainband circulation.
    for cnum in np.arange(0,endc):
        level=levels2[cnum]
        if level in overturning_levels: #If an "eyewall circulation level"
            overturning_cnums.append(cnum) #Add trajectory to the eyewall circulation
        if level not in overturning_levels: #If not an "eyewall circulation level"
            rainband_cnums.append(cnum) #Add trajectory to the rainband circulation

    #Plot isentropic streamfunction, with the eyewall circulation in red and rainband circulation in blue. 
    plt.figure(figsize=(15,10)) 
    plt.rc('axes', labelsize=40)    # fontsize of the x and y labels
    plt.rc('xtick', labelsize=40)    # fontsize of the x tick labels
    plt.rc('ytick', labelsize=40)    # fontsize of the x tick labels
    plt.rc('legend', fontsize=40)            # fontsize of the legend text    
    theta_es=np.arange(th_min, th_max, delt*2)
    [zplot, thplot]=np.meshgrid(theta_es, z) 
    ncontour = 25
    contourarray = psi.min()*((2*np.arange((ncontour+1),1.0, -1.0)-1)/(2*ncontour))
    for cnum in rainband_cnums: #Plot the rainband trajectories
        plt.plot(interpolant_th_arr[cnum],interpolant_z_arr[cnum], color='blue')#, label = 'Contour number = %s' %cnum)
        plt.xlabel('Equivalent Potential Temperature (K)')
        plt.ylabel('Height (km)')
        plt.title('Isentropic Streamfunction', fontsize=30)
    for cnum in overturning_cnums: #Plot the eyewall trajectories
        plt.plot(interpolant_th_arr[cnum],interpolant_z_arr[cnum], color='red')#, label = 'Contour number = %s' %cnum)
        plt.xlabel('Equivalent Potential Temperature (K)')
        plt.ylabel('Height (km)')
        plt.title('Isentropic Streamfunction', fontsize=30)    
    plt.title('Isentropic Streamfunction', fontsize=40)
    plt.ylabel('Height (km)')
    plt.xlabel('Equivalent Potential Temperature (K)')
    xlim(th_min, th_max)
    
    #Save some data that we will use to make figures S3 and S5
    if (Lout==600 and cval==0.82 and (SST==295 or SST==296.5 or SST==298.5)) or (Lout==600 and cval==0.85 and SST==302.5):
        np.savez("SM_ctests_1_"+np.str(SST_c)+".npz", th_min=th_min, th_max=th_max, delt=delt, interpolant_th_arr=interpolant_th_arr, interpolant_z_arr=interpolant_z_arr, psi=psi, rainband_cnums=rainband_cnums, overturning_cnums=overturning_cnums)
    if Lout==600 and cval==0.82 and SST==305.5:
        np.savez("Fig3_2_"+np.str(SST)+".npz", th_min=th_min, th_max=th_max, delt=delt, interpolant_th_arr=interpolant_th_arr, interpolant_z_arr=interpolant_z_arr, levels2=levels2, psi=psi)      
        
    #We need to rerun the interpolation code to get interpolated_t because the process above modifies the nan values in it.
    interpolated_t=[]

    for i in np.arange(endi):
        if i==0:
            interpolated_t.append(interpolator_temp(interpolant_array[i])) 
        else:
            interpolated_t.append(interpolator_temp(interpolant_array[i]))

    #Plot trajectories in temperature-entropy space, with the eyewall circulation in red and rainband circulation in blue. 
    plt.figure(figsize=(15,10)) 
    plt.rc('axes', labelsize=40)    # fontsize of the x and y labels
    plt.rc('xtick', labelsize=40)    # fontsize of the x tick labels
    plt.rc('ytick', labelsize=40)    # fontsize of the x tick labels
    plt.rc('legend', fontsize=40)            # fontsize of the legend text    
    theta_es=np.arange(th_min, th_max, delt*2)
    [zplot, thplot]=np.meshgrid(theta_es, z) 
    ncontour = 25
    contourarray = psi.min()*((2*np.arange((ncontour+1),1.0, -1.0)-1)/(2*ncontour))
    for cnum in rainband_cnums: #plots each contour
        plt.plot(interpolated_ent[cnum],interpolated_t[cnum], color='blue')#, label = 'Contour number = %s' %cnum)
        plt.xlabel('Entropy (J/(K kg))')
        plt.ylabel('Temperature (K)')
        plt.title('T-s diagram', fontsize=30)
    for cnum in overturning_cnums: #plots each contour
        plt.plot(interpolated_ent[cnum],interpolated_t[cnum], color='red')#, label = 'Contour number = %s' %cnum)
        plt.xlabel('Entropy (J/(K kg))')
        plt.ylabel('Temperature (K)')
        plt.title('T-s diagram', fontsize=30)   
    plt.xlabel('Entropy (J/(K kg))')
    plt.ylabel('Temperature (K)')
    plt.title('T-s diagram', fontsize=26) 
    

    #Calculate Eulerian streamfunction
    ncontour=25
    #Change the dimensions of dr, dz, r, and z such that they have shape (r * z)
    r=np.expand_dims(x, axis=1)
    dr1=np.diff(x)
    dr_l=dr1.tolist()
    dr_l.append(dr_l[-1])
    dr=np.asarray(dr_l)
    drn=np.expand_dims(dr, axis=1)
    for i in np.arange(len(z)):
        if i==0:
            r_padded=r
            dr_padded=drn
        else:
            r_padded=np.concatenate((r_padded, r), axis=1)
            dr_padded=np.concatenate((dr_padded, drn), axis=1)
    r_pad=np.transpose(r_padded)
    dr_pad=np.transpose(dr_padded)
    zn=np.expand_dims(z, axis=1)
    dz1=np.diff(z)
    dz_l=dz1.tolist()
    dz_l.append(dz_l[-1])
    dz=np.asarray(dz_l)
    dzn=np.expand_dims(dz, axis=1)    
    for i in np.arange(len(x)):
        if i==0:
            z_padded=zn
            dz_padded=dzn
        else:
            z_padded=np.concatenate((z_padded, zn), axis=1)
            dz_padded=np.concatenate((dz_padded, dzn), axis=1)

    utmean=np.sum(u, axis=2)/(tfinal-tstart) #Time-mean of u

    wtmean=np.sum(w, axis=2)/(tfinal-tstart) #Time-mean of w

    rhotmean=np.sum(rho, axis=2)/(tfinal-tstart) #Time-mean of rho

    streamf=streamfun(utmean,wtmean,rhotmean,r_pad,dr_pad,z_padded,dz_padded) #Calculate Eulerian streamfunction. Note that we use the dry-air density in this calculation.
    
    
    #print("Shape is:")
    
    #print(np.shape(streamf))

    #Plot Eulerian streamfunction
    plt.figure(figsize=(15,10)) 
    
    r=x
    [rplot, zplot]=np.meshgrid(r, z)
    plt.contour(rplot/1000, zplot/1000, streamf,ncontour, cmap='viridis')

    plt.rc('axes', labelsize=40)
    plt.ylabel('Height (km)', fontsize=40)
    plt.xlabel('Radial distance (km)', fontsize=40)
    plt.title("Eulerian streamfunction (kg $s^{-1}$)", fontsize=40)
    #plt.axhline(y=2, color='r', linestyle='--', linewidth=3) #OPTIONAL- line at z=2km
    plt.colorbar(format=ticker.FuncFormatter(fmt))
    
    #Save some data that we will use to make Figures S2, S3, and S4.
    if Lout==1200 and cval==0.82 and (SST==295 or SST==295.5 or SST==307 or SST==307.5):
        np.savez("SM_streamf_"+np.str(SST)+".npz", r=r, z=z, streamf=streamf, ncontour=ncontour)    
    if Lout==600 and cval==0.82 and SST==305:
        np.savez("Fig2_bbwin_"+np.str(SST)+".npz", r=r, z=z, streamf=streamf, ncontour=ncontour)  
    if Lout==600 and cval==0.82 and SST==305.5:
        np.savez("Fig3_1_"+np.str(SST)+".npz", r=r, z=z, streamf=streamf, ncontour=ncontour)      
        
        
    #OPTIONAL- Plot vertical-mean value of streamfunction at z=2km vs radius. 
    hindex=np.where(z>2000)[0][0] #Vertical index where z=2km approximately
    #print("test:")
    #print(z[hindex])
    fig, ax = plt.subplots(1, 1, figsize=(12,10))
    ax.plot(r/1000, streamf[hindex, :])
    ax.yaxis.set_major_formatter(ticker.FuncFormatter(fmt))
    ax.set_xlabel('Radial distance (km)', fontsize=40)
    ax.set_ylabel("Eulerian streamfunction (kg $s^{-1}$)", fontsize=40)   
    
    #Find surface total heat flux and its sensible and latent components
    len_r=len(x)
    len_t=tfinal-tstart    
    x_expanded=np.zeros((len_r, len_t)) #x vector but with dimensions of x * (tfinal-tstart). 
    for ti in np.arange(len_t):
        x_expanded[:, ti]=x    
    shflux_t=np.nansum(shflx*x_expanded, axis=0)/perArea #Horizontal-average surface heat flux. 
    shflux=np.nansum(shflux_t)/(tfinal-tstart) #Time-average surface heat flux
    pv_surf= psfc*Rv*qsfc/(R+Rv*qsfc) #Partial pressure of water vapor at surface
    pd_surf=psfc-pv_surf #Partial pressure of dry air at the surface
    rhosfc_moist=pd_surf/(R*SST)+pv_surf/(Rv*SST) #Density of moist air at surface
    Lvsurf=Lv0+(cpv-cpl)*(SST-T_ref) #Lv at the sea surface temperature
    lhflx=qvflx*rhosfc_moist*Lvsurf #Surface latent heat flux. Matches the bulk formulae used in CM1.
    lhflux_t=np.nansum(lhflx*x_expanded, axis=0)/perArea #Horizontal-average surface heat flux. 
    lhflux=np.nansum(lhflux_t)/(tfinal-tstart) #Time-average surface latent heat flux
    totflx=shflx+lhflx #Total surface heat flux
    totflux_t=np.nansum(totflx*x_expanded, axis=0)/perArea #Horizontal-average total surface heat flux in subdomain. 
    totflux=np.nansum(totflux_t)/(tfinal-tstart) #Time-average total surface heat flux  
    
    #Calculate mean surface precipitation rate
    pr_t=np.nansum(prate*x_expanded, axis=0)/perArea #Horizontal average
    pr=np.nansum(pr_t)/(tfinal-tstart) #Time-average

    
    #Calculate IKE
    rho_moist=pd/(R*t)+ep/(Rv*t) #Density of moist air. 
    len_r=len(x)
    len_t=tfinal-tstart
    rho_moist_25=np.squeeze(rho_moist[0, :, :]) #Density of moist air at 25m
    zsurf=0 #Note this assumes a surface with no topography
    z25=z[0] #25m height
    rho_moist_10=np.zeros((len_r, len_t))
    #Find the density of moist air at 10m via interpolation
    for xi in np.arange(len_r):
        for ti in np.arange(len_t):
            rho_moist_10[xi, ti]=np.interp(10, [zsurf, z25], [rhosfc_moist[xi, ti], rho_moist_25[xi, ti]])
    x_expanded=np.zeros((len_r, len_t)) #x vector but with dimensions of x * (tfinal-tstart)
    for ti in np.arange(len_t):
        x_expanded[:, ti]=x
    IKE_integrand=0.5*rho_moist_10*s10**2*x_expanded*dx 
    IKE_t=2*np.pi*np.nansum(IKE_integrand, axis=0) #Integrated Kinetic Energy (Powell and Reinhold, 2007, BAMS)
    IKE=np.nansum(IKE_t)/(tfinal-tstart) #Time-average. We don't perform a horizontal average here because the IKE is by definition a horizontally-integrated quantity
    
    #Find the KE per unit mass of dry air based on the maximum tangential wind speed
    #Find the maximum tangential wind speed at all times
    vmax_l=[]
    for i in np.arange(tfinal-tstart):
        vmax_t=np.max(v10[:, i])
        vmax_l.append(vmax_t)
    vmax=np.squeeze(np.asarray(vmax_l))
    #Find the density of dry air at 10m via interpolation
    rhosfc=pd_surf/(R*SST) #Density of dry air at the surface. 
    rho_25=np.squeeze(rho[0, :, :]) #Density of dry air at 25m
    rho_10=np.zeros((len_r, len_t))
    #Interpolate to get density of dry air at 10m
    for xi in np.arange(len_r):
        for ti in np.arange(len_t):
            rho_10[xi, ti]=np.interp(10, [zsurf, z25], [rhosfc[xi, ti], rho_25[xi, ti]])  
    #Get the densities of moist and dry air at the point of maximum tangential wind at all times
    rho10_l=[]
    rhom10_l=[]
    for i in np.arange(tfinal-tstart):
        vmax_c=vmax_l[i]
        xind=np.where(v10[:, i]==vmax_c)
        rho10=rho_10[xind, i]
        rhom10=rho_moist_10[xind, i]
        rho10_l.append(rho10)
        rhom10_l.append(rhom10)
    rho10_a=np.squeeze(np.asarray(rho10_l))
    rhom10_a=np.squeeze(np.asarray(rhom10_l))
    #print("Time-mean vmax is:")
    #print(np.nansum(vmax)/(tfinal-tstart))
    KE_permass= 0.5*(vmax**2)*(rhom10_a/rho10_a) #The last term converts the KE per unit mass of humid air, 0.5*(vmax**2), to KE per unit mass of dry air- for ease of comparison to WKE
    KE_pm=np.nansum(KE_permass)/(tfinal-tstart) #Time-average
    #print("KE_pm is:")
    #print(KE_pm)   

    #Get rid of nan values in all "timeseries" derived from each trajectory. This prepares the trajectories for the code that calculates the MAFALDA-derived energetic 
    #and efficiency quantities Wmax, WKE, etc. If "nan" values are not removed then the code returns "nan" values or fails when finding these quantities.
    
    #First, we remove nans for the variables used to find Wmax- which for each trajectory is the closed line integral of Tds
    #Remove nans from moist entropy "timeseries"
    nansum=0
    ind=0
    for cnum in np.arange(0, endc): #Loop through all trajectories
        nansum_c=sum(np.isnan(interpolated_ent[cnum])) #Number of "nan" values in the "timeseries" of moist entropy derived from the current trajectory
        if nansum_c != len(interpolated_ent[cnum]): #Proceed if the current "timeseries" is not entirely formed from pairs of nan values 
            if (size(interpolated_ent[cnum])>2) and (sum(np.isnan(interpolated_ent[cnum]))<size(interpolated_ent[cnum])-2): #Proceed if more than two non-nan points exist
                interpolated_ent[cnum]=average_nans_cnum(interpolated_ent[cnum])
            if (sum(np.isnan(interpolated_ent[cnum]))>size(interpolated_ent[cnum])-3): #only 1-2 non-nan points exist in the "timeseries"
                #Set all non-nan values to nan because these arrays correspond to single points or lines in temperature-entropy space and so should contribute nothing the closed line integral of Tds
                for i in np.arange(0, len(interpolated_ent[cnum])):
                    if not np.isnan(interpolated_ent[cnum][i]):
                        interpolated_ent[cnum][i]=nan              
    #Repeat for other thermodynamic "timeseries": temperature, pressure, etc.
    #Temperature
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_t[cnum])) 
        if nansum_c != len(interpolated_t[cnum]): 
            if (size(interpolated_t[cnum])>2) and (sum(np.isnan(interpolated_t[cnum]))<size(interpolated_t[cnum])-2): 
                interpolated_t[cnum]=average_nans_cnum(interpolated_t[cnum])
            if (sum(np.isnan(interpolated_t[cnum]))>size(interpolated_t[cnum])-3): 
                for i in np.arange(0, len(interpolated_t[cnum])):
                    if not np.isnan(interpolated_t[cnum][i]):
                        interpolated_t[cnum][i]=nan              
    #Remove nans from variables used to find W- which for each trajectory is the closed line integral of alpha_d dp
    #Pressure
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_p[cnum])) 
        if nansum_c != len(interpolated_p[cnum]): 
            if (size(interpolated_p[cnum])>2) and (sum(np.isnan(interpolated_p[cnum]))<size(interpolated_p[cnum])-2):
                interpolated_p[cnum]=average_nans_cnum(interpolated_p[cnum])
            if (sum(np.isnan(interpolated_p[cnum]))>size(interpolated_p[cnum])-3): 
                for i in np.arange(0, len(interpolated_p[cnum])):
                    if not np.isnan(interpolated_p[cnum][i]):
                        interpolated_p[cnum][i]=nan               
    #Specific volume
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_ad[cnum])) 
        if nansum_c != len(interpolated_ad[cnum]): 
            if (size(interpolated_ad[cnum])>2) and (sum(np.isnan(interpolated_ad[cnum]))<size(interpolated_ad[cnum])-2): 
                interpolated_ad[cnum]=average_nans_cnum(interpolated_ad[cnum])
            if (sum(np.isnan(interpolated_ad[cnum]))>size(interpolated_ad[cnum])-3): 
                for i in np.arange(0, len(interpolated_ad[cnum])):
                    if not np.isnan(interpolated_ad[cnum][i]):
                        interpolated_ad[cnum][i]=nan     
    #Remove nans from variables used to find Wp- which for each trajectory is the closed line integral of WP_integral dz
    #Height
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolant_z_arr[cnum])) 
        if nansum_c != len(interpolant_z_arr[cnum]): 
            if (size(interpolant_z_arr[cnum])>2) and (sum(np.isnan(interpolant_z_arr[cnum]))<size(interpolant_z_arr[cnum])-2): 
                interpolant_z_arr[cnum]=average_nans_cnum(interpolant_z_arr[cnum])
            if (sum(np.isnan(interpolant_z_arr[cnum]))>size(interpolant_z_arr[cnum])-3): 
                for i in np.arange(0, len(interpolant_z_arr[cnum])):
                    if not np.isnan(interpolant_z_arr[cnum][i]):
                        interpolant_z_arr[cnum][i]=nan             
    #WP_integral
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_WPint[cnum])) 
        if nansum_c != len(interpolated_WPint[cnum]):  
            if (size(interpolated_WPint[cnum])>2) and (sum(np.isnan(interpolated_WPint[cnum]))<size(interpolated_WPint[cnum])-2): 
                interpolated_WPint[cnum]=average_nans_cnum(interpolated_WPint[cnum])
            if (sum(np.isnan(interpolated_WPint[cnum]))>size(interpolated_WPint[cnum])-3): 
                for i in np.arange(0, len(interpolated_WPint[cnum])):
                    if not np.isnan(interpolated_WPint[cnum][i]):
                        interpolated_WPint[cnum][i]=nan    
    #Remove nans from variables used to find Delta(G)- which for each trajectory is the sum of the closed line integrals of g_w dq_w, w=v, l, i
    #Mixing ratio of water vapor
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_qv[cnum])) 
        if nansum_c != len(interpolated_qv[cnum]): 
            if (size(interpolated_qv[cnum])>2) and (sum(np.isnan(interpolated_qv[cnum]))<size(interpolated_qv[cnum])-2): 
                interpolated_qv[cnum]=average_nans_cnum(interpolated_qv[cnum])
            if (sum(np.isnan(interpolated_qv[cnum]))>size(interpolated_qv[cnum])-3): 
                for i in np.arange(0, len(interpolated_qv[cnum])):
                    if not np.isnan(interpolated_qv[cnum][i]):
                        interpolated_qv[cnum][i]=nan
    #Gibbs free energy of water vapor
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_gv[cnum])) 
        if nansum_c != len(interpolated_gv[cnum]): 
            if (size(interpolated_gv[cnum])>2) and (sum(np.isnan(interpolated_gv[cnum]))<size(interpolated_gv[cnum])-2): 
                interpolated_gv[cnum]=average_nans_cnum(interpolated_gv[cnum])
            if (sum(np.isnan(interpolated_gv[cnum]))>size(interpolated_gv[cnum])-3): 
                for i in np.arange(0, len(interpolated_gv[cnum])):
                    if not np.isnan(interpolated_gv[cnum][i]):
                        interpolated_gv[cnum][i]=nan                        
    #Mixing ratio of solid water
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_qi[cnum])) 
        if nansum_c != len(interpolated_qi[cnum]):  
            if (size(interpolated_qi[cnum])>2) and (sum(np.isnan(interpolated_qi[cnum]))<size(interpolated_qi[cnum])-2): 
                interpolated_qi[cnum]=average_nans_cnum(interpolated_qi[cnum])
            if (sum(np.isnan(interpolated_qi[cnum]))>size(interpolated_qi[cnum])-3): 
                for i in np.arange(0, len(interpolated_qi[cnum])):
                    if not np.isnan(interpolated_qi[cnum][i]):
                        interpolated_qi[cnum][i]=nan
    #Gibbs free energy of solid water
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_gi[cnum])) 
        if nansum_c != len(interpolated_gi[cnum]):  
            if (size(interpolated_gi[cnum])>2) and (sum(np.isnan(interpolated_gi[cnum]))<size(interpolated_gi[cnum])-2): 
                interpolated_gi[cnum]=average_nans_cnum(interpolated_gi[cnum])
            if (sum(np.isnan(interpolated_gi[cnum]))>size(interpolated_gi[cnum])-3): 
                for i in np.arange(0, len(interpolated_gi[cnum])):
                    if not np.isnan(interpolated_gi[cnum][i]):
                        interpolated_gi[cnum][i]=nan
    #Mixing ratio of liquid water
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_ql[cnum])) 
        if nansum_c != len(interpolated_ql[cnum]):  
            if (size(interpolated_ql[cnum])>2) and (sum(np.isnan(interpolated_ql[cnum]))<size(interpolated_ql[cnum])-2): 
                interpolated_ql[cnum]=average_nans_cnum(interpolated_ql[cnum])
            if (sum(np.isnan(interpolated_ql[cnum]))>size(interpolated_ql[cnum])-3):
                for i in np.arange(0, len(interpolated_ql[cnum])):
                    if not np.isnan(interpolated_ql[cnum][i]):
                        interpolated_ql[cnum][i]=nan
    #Gibbs free energy of liquid water
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_gl[cnum])) 
        if nansum_c != len(interpolated_gl[cnum]): 
            if (size(interpolated_gl[cnum])>2) and (sum(np.isnan(interpolated_gl[cnum]))<size(interpolated_gl[cnum])-2): 
                interpolated_gl[cnum]=average_nans_cnum(interpolated_gl[cnum])
            if (sum(np.isnan(interpolated_gl[cnum]))>size(interpolated_gl[cnum])-3): 
                for i in np.arange(0, len(interpolated_gl[cnum])):
                    if not np.isnan(interpolated_gl[cnum][i]):
                        interpolated_gl[cnum][i]=nan
    #OPTIONAL- remove nan values from those optionally-calculated "timeseries" that can be used to calculate MAFALDA- derived energetic quantities, or portions of these
    #Contribution to moist entropy from relative humidity. The user can use this to calculate the contribution from relative humidity to Wmax
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_ent_RH[cnum])) 
        if nansum_c != len(interpolated_ent_RH[cnum]): 
            if (size(interpolated_ent_RH[cnum])>2) and (sum(np.isnan(interpolated_ent_RH[cnum]))<size(interpolated_ent_RH[cnum])-2): 
                interpolated_ent_RH[cnum]=average_nans_cnum(interpolated_ent_RH[cnum])
            if (sum(np.isnan(interpolated_ent_RH[cnum]))>size(interpolated_ent_RH[cnum])-3): 
                for i in np.arange(0, len(interpolated_ent_RH[cnum])):
                    if not np.isnan(interpolated_ent_RH[cnum][i]):
                        interpolated_ent_RH[cnum][i]=nan
    #Contribution to moist entropy not from relative humidity. The user can use this to calculate the contribution from non-relative humidity variables to Wmax
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_ent_nRH[cnum])) 
        if nansum_c != len(interpolated_ent_nRH[cnum]): 
            if (size(interpolated_ent_nRH[cnum])>2) and (sum(np.isnan(interpolated_ent_nRH[cnum]))<size(interpolated_ent_nRH[cnum])-2): 
                interpolated_ent_nRH[cnum]=average_nans_cnum(interpolated_ent_nRH[cnum])
            if (sum(np.isnan(interpolated_ent_nRH[cnum]))>size(interpolated_ent_nRH[cnum])-3): 
                for i in np.arange(0, len(interpolated_ent_nRH[cnum])):
                    if not np.isnan(interpolated_ent_nRH[cnum][i]):
                        interpolated_ent_nRH[cnum][i]=nan
    #Moist enthalpy. The closed line integral of the enthalpy, together with the closed line integral of alpha_d dp, can be alternatively used to calculate the heat 
    #input and output Qin and Qout below, as in Pauluis and Zhang (2017, JAS) equation (3)
    nansum=0
    ind=0
    for cnum in np.arange(0, endc):
        nansum_c=sum(np.isnan(interpolated_h[cnum])) 
        if nansum_c != len(interpolated_h[cnum]): 
            if (size(interpolated_h[cnum])>2) and (sum(np.isnan(interpolated_h[cnum]))<size(interpolated_h[cnum])-2): 
                interpolated_h[cnum]=average_nans_cnum(interpolated_h[cnum])
            if (sum(np.isnan(interpolated_h[cnum]))>size(interpolated_h[cnum])-3): 
                for i in np.arange(0, len(interpolated_h[cnum])):
                    if not np.isnan(interpolated_h[cnum][i]):
                        interpolated_h[cnum][i]=nan   

    #Get the value of the 'mass circulation' for each level of the isentropic streamfunction, see equation (11) in the main text                    
    psi_min=psi.min() #Minimum of isentropic streamfunction
    mass_circ=-psi_min/ncontour #Mass circulation
    
    #Calculate MAFALDA-derived energetic quantities: Wmax, W, Wp, etc.
    Tds_clat=[] #Wmax at all isentropic streamfunction levels
    addp_clat=[] #W at all isentropic streamfunction levels
    dWp_clat=[] #Wp at all isentropic streamfunction levels
    gvdqv_clat=[] #Contribution to Delta(G) from water vapor at all isentropic streamfunction levels
    gldql_clat=[] #Contribution to Delta(G) from liquid water at all isentropic streamfunction levels
    gidqi_clat=[] #Contribution to Delta(G) from solid water at all isentropic streamfunction levels
    addp_clat_2=[] #Same as addp_clat but in W/m2 rather than J/kg
    dWp_clat_2=[] #Same as dWp_clat but in W/m2 rather than J/kg
    gvdqv_clat_2=[] #Same as gvdqv_clat but in W/m2 rather than J/kg
    gldql_clat_2=[] #Same as gldql_clat but in W/m2 rather than J/kg
    gidqi_clat_2=[] #Same as gidqi_clat but in W/m2 rather than J/kg
    firstlevel_flag=0 #Tracks whether or not the current trajectory corresponds to the first trajectory at the first level of the isentropic streamfunction
    for cnum in np.arange(0, endc): #Loop through all MAFALDA trajectories
        if len(interpolated_t[cnum])>2: #If more than 2 points exist in the trajectory
            #Calculate Wmax, W, Wp, and all contributions to Delta(G) for this trajectory
            [Tds_cnum, addp_cnum, dWp_cnum, gvdqv_cnum, gldql_cnum, gidqi_cnum]=MAFALDA(interpolated_t[cnum], interpolated_ent[cnum], interpolated_ad[cnum], interpolated_p[cnum], interpolated_WPint[cnum], interpolant_z_arr[cnum], interpolated_gv[cnum], interpolated_qv[cnum], interpolated_gl[cnum], interpolated_ql[cnum], interpolated_gi[cnum], interpolated_qi[cnum])
            if (firstlevel_flag==1)&(cnum!=endc-1): #If we are not at the first level's first trajectory and not at the last level's last trajectory, proceed as follows
                if levels2[cnum]!=levels2[cnum-1]: #If we have just changed levels
                    #Save the values of all energetic variables at the previous level of the isentropic streamfunction.
                    #Then, begin summing the energetic variables over this current level.
                    Tds_clat.append(Tds_clevel) #e.g., Save the value of Wmax for the previous level 
                    Tds_clevel=Tds_cnum #e.g., Initialize the sum of Wmax values for the current level with the value of Wmax we just calculated
                    addp_clat.append(addp_clevel)
                    dWp_clat.append(dWp_clevel)
                    gvdqv_clat.append(gvdqv_clevel)
                    gldql_clat.append(gldql_clevel)
                    gidqi_clat.append(gidqi_clevel) 
                    #Find W, Wp, etc., in W/m2 for the current level of the isentropic streamfunction following equation (10) in the main text
                    addp_clat_2.append(addp_clevel*mass_circ) 
                    dWp_clat_2.append(dWp_clevel*mass_circ) 
                    gvdqv_clat_2.append(gvdqv_clevel*mass_circ) 
                    gldql_clat_2.append(gldql_clevel*mass_circ) 
                    gidqi_clat_2.append(gidqi_clevel*mass_circ) 
                    
                    addp_clevel=addp_cnum
                    dWp_clevel=dWp_cnum
                    gvdqv_clevel=gvdqv_cnum
                    gldql_clevel=gldql_cnum
                    gidqi_clevel=gidqi_cnum                     
                else: #If we have not changed levels
                    #Add the values of all energetic variables that were calculated for this trajectory to the sum for the current level
                    Tds_clevel+=Tds_cnum #e.g., add the value of Wmax for the current trajectory to the values of Wmax for other trajectories at this level
                    addp_clevel+=addp_cnum
                    dWp_clevel+=dWp_cnum
                    gvdqv_clevel+=gvdqv_cnum
                    gldql_clevel+=gldql_cnum
                    gidqi_clevel+=gidqi_cnum
            elif (firstlevel_flag==0): #If we are at the first level of the isentropic streamfunction, initialize the variables Tds_clevel, etc.
                #Initialize the sum of the energetic variables over the first level.
                Tds_clevel=Tds_cnum #e.g., Initialize the sum of Wmax values for the first level with the value of Wmax we just calculated
                addp_clevel=addp_cnum
                dWp_clevel=dWp_cnum
                gvdqv_clevel=gvdqv_cnum
                gldql_clevel=gldql_cnum
                gidqi_clevel=gidqi_cnum 
                firstlevel_flag=1 #Change the value of firstlevel_flag so that we do not re-initialize variables for the next trajectory
            elif (firstlevel_flag==1)&(cnum==endc-1): #If we are at the last level's last trajectory
                if levels2[cnum]!=levels2[cnum-1]: #If the last trajectory corresponds to a new level
                    #Save the values of all energetic variables at the previous level of the isentropic streamfunction.
                    #Then, save the values of all energetic variables at the current level of the isentropic streamfunction.                   
                    Tds_clat.append(Tds_clevel) #e.g., Save the value of Wmax for the previous level
                    Tds_clat.append(Tds_cnum) #e.g., Save the value of Wmax for the current level
                    addp_clat.append(addp_clevel)
                    addp_clat.append(addp_cnum)
                    dWp_clat.append(dWp_clevel)
                    dWp_clat.append(dWp_cnum)
                    gvdqv_clat.append(gvdqv_clevel)
                    gvdqv_clat.append(gvdqv_cnum)
                    gldql_clat.append(gldql_clevel)
                    gldql_clat.append(gldql_cnum)
                    gidqi_clat.append(gidqi_clevel)
                    gidqi_clat.append(gidqi_cnum)
                    #Variables in W/m2, see above
                    addp_clat_2.append(addp_clevel*mass_circ) 
                    addp_clat_2.append(addp_cnum*mass_circ)
                    dWp_clat_2.append(dWp_clevel*mass_circ) 
                    dWp_clat_2.append(dWp_cnum*mass_circ) 
                    gvdqv_clat_2.append(gvdqv_clevel*mass_circ)
                    gvdqv_clat_2.append(gvdqv_cnum*mass_circ)
                    gldql_clat_2.append(gldql_clevel*mass_circ) 
                    gldql_clat_2.append(gldql_cnum*mass_circ)
                    gidqi_clat_2.append(gidqi_clevel*mass_circ) 
                    gidqi_clat_2.append(gidqi_cnum*mass_circ)
                else: #If the last trajectory does not correspond to a new level
                    #Save the values of all energetic variables at the current level of the isentropic streamfunction.
                    Tds_clat.append(Tds_clevel+Tds_cnum) #e.g., Save the value of Wmax for the current level
                    addp_clat.append(addp_clevel+addp_cnum)
                    dWp_clat.append(dWp_clevel+dWp_cnum)
                    gvdqv_clat.append(gvdqv_clevel+gvdqv_cnum)
                    gldql_clat.append(gldql_clevel+gldql_cnum)
                    gidqi_clat.append(gidqi_clevel+gidqi_cnum)
                    #Variables in W/m2, see above
                    addp_clat_2.append((addp_clevel+addp_cnum)*mass_circ)
                    dWp_clat_2.append((dWp_clevel+dWp_cnum)*mass_circ)
                    gvdqv_clat_2.append((gvdqv_clevel+gvdqv_cnum)*mass_circ)
                    gldql_clat_2.append((gldql_clevel+gldql_cnum)*mass_circ)
                    gidqi_clat_2.append((gidqi_clevel+gidqi_cnum)*mass_circ)
            else:
                print("ERROR!!!- unexpected condition met in MAFALDA section")
    #Calculate MAFALDA-derived energetic quantities as average values over all levels of the isentropic streamfunction.
    Tds=np.nanmean(Tds_clat) #Wmax
    addp=np.nanmean(addp_clat) #W
    dWp=np.nanmean(dWp_clat) #Wp
    dWKE_clat_arr=np.asarray(addp_clat)-np.asarray(dWp_clat) #WKE at all isentropic streamfunction levels
    dWKE_clat=dWKE_clat_arr.tolist() 
    dWKE=np.nanmean(dWKE_clat) #WKE
    gvdqv=np.nanmean(gvdqv_clat) #Contribution to Delta(G) from water vapor
    gldql=np.nanmean(gldql_clat) #Contribution to Delta(G) from liquid water
    gidqi=np.nanmean(gidqi_clat) #Contribution to Delta(G) from solid water
    #Variables in W/m2, calculated following equation (10) in the main text, see above
    dWp_2=np.nansum(dWp_clat_2)
    dWKE_clat_arr_2=np.asarray(addp_clat_2)-np.asarray(dWp_clat_2) 
    dWKE_clat_2=dWKE_clat_arr_2.tolist() 
    dWKE_2=np.nansum(dWKE_clat_2) 
    
    dg_clat=np.asarray(gvdqv_clat)+np.asarray(gidqi_clat)+np.asarray(gldql_clat) #Gibbs penalty Delta(G) at all isentropic streamfunction levels
    dg=np.nanmean(dg_clat) #Gibbs penalty Delta(G)
    #As above, but in W/m2 following equation (10) of the main text
    dg_clat_2=np.asarray(gvdqv_clat_2)+np.asarray(gidqi_clat_2)+np.asarray(gldql_clat_2) 
    dg_2=np.nansum(dg_clat_2)    
    

    #Calculate the heat input and output, and their associated temperatures. For this, we define the external heating/cooling
    #of a small mass of air as equal to Tds+sum_over_w=v,l, i (g_w dq_w), as in Pauluis and Zhang (2017, JAS) equation (7)
    Qin_clat=[] #Heat input Qin at all isentropic streamfunction levels
    Qout_clat=[] #Heat output Qout at all isentropic streamfunction levels
    Tin_clat=[] #Temperature of heat input Tin at all isentropic streamfunction levels
    Tout_clat=[] #Temperature of heat output Tout at all isentropic streamfunction levels
    Qin_Tin_clat=[] #Qin/Tin at all isentropic streamfunction levels
    Qout_Tout_clat=[] #Qout/Tout at all isentropic streamfunction levels     
    Qin_clat_2=[] #Same as Qin_clat, but in W/m2
    for cnum in np.arange(0, endc): #Loop through all MAFALDA trajectories
        if len(interpolated_t[cnum])>2: #If more than 2 points exist in the trajectory
            #print("cnum is "+np.str(cnum))
            #Calculate Qin, Qin/Tin, Qout, and Qout/Tout for the current trajectory, following a modifed version of the procedure in Pauluis and Zhang (2017, JAS)
            [Qin_cnum, Qin_Tin_cnum]=getQin(interpolated_t[cnum], interpolated_ent[cnum], interpolated_gv[cnum], interpolated_qv[cnum], interpolated_gl[cnum], interpolated_ql[cnum], interpolated_gi[cnum], interpolated_qi[cnum])
            [Qout_cnum, Qout_Tout_cnum]=getQout(interpolated_t[cnum], interpolated_ent[cnum], interpolated_gv[cnum], interpolated_qv[cnum], interpolated_gl[cnum], interpolated_ql[cnum], interpolated_gi[cnum], interpolated_qi[cnum])
            #We calculated Qin/Tin and Qout/Tout instead of Tin and Tout here because our methodology involves summing over all energetic quantities at a given level of the isentropic streamfunction.
            #While it is appropriate to apply such a methodology to energetic and energy-related quantities like Qin and Qin/Tin, it is not appropriate to sum over an instrinsic variable such as temperature.
            if (cnum!=0)&(cnum!=endc-1): #If we are not at the first level's first trajectory and not at the last level's last trajectory, proceed as follows
                if levels2[cnum]!=levels2[cnum-1]: #If we have just changed levels
                    Tin_clevel=Qin_clevel/Qin_Tin_clevel #Each time a level finishes, calculate Tin and Tout for that level using the sums of Qin, Qin/Tin, Qout, and Qout/Tout for that level
                    if np.abs(Qin_Tin_clevel)<10**(-15): #We don't want to divide by zero or a very small number that is effectively zero
                        Tin_clevel=0 #Set Tin to zero if Qin/Tin is very small or equal to zero
                    Tout_clevel=Qout_clevel/Qout_Tout_clevel
                    if np.abs(Qout_Tout_clevel)<10**(-15):
                        Tout_clevel=0
                    #Save the values of Qin (J/kg and W/m2), Qout, Qin/Tin, Qout/Tout, Tin, and Tout at the previous level of the isentropic streamfunction.  
                    #Then, begin summing the energetic and energy-related variables for this current level.
                    Qin_clat.append(Qin_clevel)
                    Qin_clat_2.append(Qin_clevel*mass_circ)
                    Qout_clat.append(Qout_clevel)
                    Qin_Tin_clat.append(Qin_Tin_clevel)
                    Qout_Tout_clat.append(Qout_Tout_clevel)
                    Tin_clat.append(Tin_clevel) 
                    Tout_clat.append(Tout_clevel)
                    Qin_clevel=Qin_cnum
                    Qin_Tin_clevel=Qin_Tin_cnum                
                    Qout_clevel=Qout_cnum  
                    Qout_Tout_clevel=Qout_Tout_cnum                                           
                else: #If we have not changed levels
                    #Add the values of all variables that were calculated for this trajectory to the sum for the current level
                    Qin_clevel+=Qin_cnum
                    Qin_Tin_clevel+=Qin_Tin_cnum
                    Qout_clevel+=Qout_cnum
                    Qout_Tout_clevel+=Qout_Tout_cnum
            elif (cnum==0): #If we are at the first level of the isentropic streamfunction, initialize the variables Qin_clevel, etc.
                #Initialize the sum of the variables for the first level.
                Qin_clevel=Qin_cnum
                Qin_Tin_clevel=Qin_Tin_cnum
                Qout_clevel=Qout_cnum
                Qout_Tout_clevel=Qout_Tout_cnum
            elif (cnum==endc-1): #If we are at the last level's last trajectory
                if levels2[cnum]!=levels2[cnum-1]: #If the last trajectory corresponds to a new level
                    Tin_clevel=Qin_clevel/Qin_Tin_clevel #Calculate Tin and Tout for the previous level
                    if np.abs(Qin_Tin_clevel)<10**(-15): 
                        Tin_clevel=0
                    Tout_clevel=Qout_clevel/Qout_Tout_clevel
                    if np.abs(Qout_Tout_clevel)<10**(-15):
                        Tout_clevel=0  
                    #Save the values of Qin (J/kg and W/m2), Qout, Qin/Tin, Qout/Tout, Tin, and Tout at the previous and current levels of the isentropic streamfunction.                         
                    Qin_clat.append(Qin_clevel)  
                    Qin_clat_2.append(Qin_clevel*mass_circ)
                    Qout_clat.append(Qout_clevel) 
                    Qin_Tin_clat.append(Qin_Tin_clevel)
                    Qout_Tout_clat.append(Qout_Tout_clevel) 
                    Tin_clat.append(Tin_clevel)
                    Tout_clat.append(Tout_clevel)                     
                    Qin_clat.append(Qin_cnum) 
                    Qin_clat_2.append(Qin_cnum*mass_circ) 
                    Qout_clat.append(Qout_cnum) 
                    Qin_Tin_clat.append(Qin_Tin_cnum)
                    Qout_Tout_clat.append(Qout_Tout_cnum)
                    Tin_clevel=Qin_cnum/Qin_Tin_cnum #Calculate Tin and Tout for the current level
                    if np.abs(Qin_Tin_cnum)<10**(-15): 
                        Tin_cnum=0                    
                    Tout_clevel=Qout_cnum/Qout_Tout_cnum
                    if np.abs(Qout_Tout_cnum)<10**(-15):
                        Tout_cnum=0                       
                    Tin_clat.append(Tin_clevel)
                    Tout_clat.append(Tout_clevel)                     
                else: #If the last trajectory does not correspond to a new level
                    Tin_clevel=(Qin_clevel+Qin_cnum)/(Qin_Tin_clevel+Qin_Tin_cnum) #Calculate Tin and Tout for the current level, 
                                                                                   #including using the values of Qin, etc. for the 
                                                                                   #current trajectory 
                    if np.abs(Qin_Tin_clevel+Qin_Tin_cnum)<10**(-15):
                        Tin_clevel=0
                    Tout_clevel=(Qout_clevel+Qout_cnum)/(Qout_Tout_clevel+Qout_Tout_cnum)
                    if np.abs(Qout_Tout_clevel+Qout_Tout_cnum)<10**(-15):
                        Tout_clevel=0
                    Qin_clevel+=Qin_cnum #Add the current values of Qin and Qout to the sum for this level
                    Qout_clevel+=Qout_cnum
                    Qin_Tin_clevel+=Qin_Tin_cnum
                    Qout_Tout_clevel+=Qout_Tout_cnum 
                    #Save the values of Qin (J/kg and W/m2), Qout, Qin/Tin, Qout/Tout, Tin, and Tout at the current level of the isentropic streamfunction.                        
                    Qin_clat.append(Qin_clevel)
                    Qin_clat_2.append(Qin_clevel*mass_circ)
                    Qout_clat.append(Qout_clevel)
                    Qin_Tin_clat.append(Qin_Tin_clevel)
                    Qout_Tout_clat.append(Qout_Tout_clevel)
                    Tin_clat.append(Tin_clevel)
                    Tout_clat.append(Tout_clevel)                                       
    #Calculate Qin, Qout, Qin/Tin, and Qout/Tout as average values over all levels of the isentropic streamfunction.
    Qin=np.nanmean(Qin_clat) #Heat input
    Qin_2=np.nansum(Qin_clat_2) #Qin in W/m2
    Qin_Tin=np.nanmean(Qin_Tin_clat) #Qin/Tin
    Qout=np.nanmean(Qout_clat) #Heat output
    Qout_Tout=np.nanmean(Qout_Tout_clat) #Qout/Tout
    #Calculate Tin and Tout
    Tin=Qin/Qin_Tin #Heat input temperature
    Tin_clat=np.asarray(Qin_clat)/np.asarray(Qin_Tin_clat)
    Tout=Qout/Qout_Tout #Heat output temperature
    Tout_clat=np.asarray(Qout_clat)/np.asarray(Qout_Tout_clat)
    #Calculate Carnot efficiency, as in Pauluis and Zhang (2017, JAS) equation (18)
    eta_c_clat=(Tin_clat-Tout_clat)/Tin_clat #Carnot efficiency at all isentropic streamfunction levels
    eta_c=(Tin-Tout)/Tin #Carnot efficiency
    
    mech_eff=np.asarray(dWKE_clat)/np.asarray(Qin_clat) #Mechanical efficiency at all isentropic streamfunction levels    

    #Now, we check that the MAFALDA equalty Wmax=W+Delta(G) holds to within 5%
    work_clat_3=np.asarray(addp_clat)-np.asarray(dg_clat) #W+Delta(G) at all isentropic streamfunction levels 
    ratio=work_clat_3/np.asarray(Tds_clat) #Wmax/(W+Delta(G)) at all isentropic streamfunction levels 
    #OPTIONAL- plot the ratio Wmax/(W+Delta(G)) against the corresponding level of the isentropic streamfunction
    plt.rc('figure', titlesize=20)     # fontsize of the figure title.   
    plt.rc('axes', labelsize=20)    # fontsize of the x and y labels
    plt.rc('xtick', labelsize=20)    # fontsize of the x tick labels
    plt.rc('ytick', labelsize=20)    # fontsize of the x tick labels     
    plt.figure(figsize=(15,10)) 
    plt.plot(np.arange(len(ratio), 0, -1), ratio)
    plt.ylabel('Ratio between $W_{Max}$ and W+$\Delta$G')
    plt.xlabel('Cycle')
    plt.title("Ratio of RHS to LHS of MAFALDA equality, vs cycle", fontsize=20)
    plt.grid() #adds gridlines to the plot
    plt.show()


    test_equality=(addp-dg)/Tds #Wmax/(W+Delta(G)) based on the average values over all isentropic streamfunction levels
    
    if (test_equality<1.05) and (test_equality>0.95): #If the MAFALDA equality holds to within 5%
        print("MAFALDA equality holds!")
        print(test_equality)
    else: #If the MAFALDA equality does not hold to within 5%
        if (test_equality<1.1) and (test_equality>0.9): #If the MAFALDA equality holds to within 10%
            print("WARNING- MAFALDA equality holds to within only 10%")
            print(test_equality)
        else:
            print("ERROR!!!- MAFALDA equality does not hold!")
            print(test_equality)

    #Repeat the above procedure for the eyewall circulation only
    
    Tds_clat_ov=[] #Wmax for the eyewall circulation at all corresponding levels of the isentropic streamfunction
    addp_clat_ov=[] #W for the eyewall circulation at all corresponding levels of the isentropic streamfunction
    dWp_clat_ov=[] #Wp for the eyewall circulation at all corresponding levels of the isentropic streamfunction
    gvdqv_clat_ov=[] #Contribution to Delta(G) from water vapor for the eyewall circulation at all corresponding levels of the isentropic streamfunction
    gldql_clat_ov=[] #Contribution to Delta(G) from liquid water for the eyewall circulation at all corresponding levels of the isentropic streamfunction
    gidqi_clat_ov=[] #Contribution to Delta(G) from solid water for the eyewall circulation at all corresponding levels of the isentropic streamfunction
    for cnum in overturning_cnums: #Loop through all eyewall trajectories
        if len(interpolated_t[cnum])>2: 
            [Tds_cnum_ov, addp_cnum_ov, dWp_cnum_ov, gvdqv_cnum_ov, gldql_cnum_ov, gidqi_cnum_ov]=MAFALDA(interpolated_t[cnum], interpolated_ent[cnum], interpolated_ad[cnum], interpolated_p[cnum], interpolated_WPint[cnum], interpolant_z_arr[cnum], interpolated_gv[cnum], interpolated_qv[cnum], interpolated_gl[cnum], interpolated_ql[cnum], interpolated_gi[cnum], interpolated_qi[cnum])
            if len(overturning_cnums)==1: #If only one eyewall trajectory exists, proceed as follows:
                #Set the value of each energetic variable at the current and only eyewall level of the isentropic streamfunction to the values that we just calculated for the current trajectory
                Tds_clat_ov=Tds_cnum_ov
                addp_clat_ov=addp_cnum_ov
                dWp_clat_ov=dWp_cnum_ov
                gvdqv_clat_ov=gvdqv_cnum_ov
                gldql_clat_ov=gldql_cnum_ov
                gidqi_clat_ov=gidqi_cnum_ov
            else: #If more than one eyewall trajectory exists, proceed as follows:
                if (cnum!=overturning_cnums[0])&(cnum!=overturning_cnums[-1]): #If we are not at the first eyewall level's first trajectory and not at the last eyewall level's last trajectory
                    if levels2[cnum]!=levels2[last_cnum]: #If we have just changed levels
                        Tds_clat_ov.append(Tds_clevel_ov)
                        Tds_clevel_ov=Tds_cnum_ov
                        addp_clat_ov.append(addp_clevel_ov)
                        addp_clevel_ov=addp_cnum_ov
                        dWp_clat_ov.append(dWp_clevel_ov)
                        dWp_clevel_ov=dWp_cnum_ov
                        gvdqv_clat_ov.append(gvdqv_clevel_ov)
                        gvdqv_clevel_ov=gvdqv_cnum_ov
                        gldql_clat_ov.append(gldql_clevel_ov)
                        gldql_clevel_ov=gldql_cnum_ov
                        gidqi_clat_ov.append(gidqi_clevel_ov)
                        gidqi_clevel_ov=gidqi_cnum_ov 
                        last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
                    else:
                        Tds_clevel_ov+=Tds_cnum_ov
                        addp_clevel_ov+=addp_cnum_ov
                        dWp_clevel_ov+=dWp_cnum_ov
                        gvdqv_clevel_ov+=gvdqv_cnum_ov
                        gldql_clevel_ov+=gldql_cnum_ov
                        gidqi_clevel_ov+=gidqi_cnum_ov
                        last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
                elif (cnum==overturning_cnums[0]): #If we are at the first eyewall level of the isentropic streamfunction, initialize the variables Tds_clevel_ov, etc.
                    Tds_clevel_ov=Tds_cnum_ov
                    addp_clevel_ov=addp_cnum_ov
                    dWp_clevel_ov=dWp_cnum_ov
                    gvdqv_clevel_ov=gvdqv_cnum_ov
                    gldql_clevel_ov=gldql_cnum_ov
                    gidqi_clevel_ov=gidqi_cnum_ov
                    last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
                elif (cnum==overturning_cnums[-1]): #If we are at the last eyewall level's last trajectory
                    if levels2[cnum]!=levels2[last_cnum]: #If the last trajectory corresponds to a new level
                        Tds_clat_ov.append(Tds_clevel_ov)
                        Tds_clat_ov.append(Tds_cnum_ov)
                        addp_clat_ov.append(addp_clevel_ov)
                        addp_clat_ov.append(addp_cnum_ov)
                        dWp_clat_ov.append(dWp_clevel_ov)
                        dWp_clat_ov.append(dWp_cnum_ov)
                        gvdqv_clat_ov.append(gvdqv_clevel_ov)
                        gvdqv_clat_ov.append(gvdqv_cnum_ov)
                        gldql_clat_ov.append(gldql_clevel_ov)
                        gldql_clat_ov.append(gldql_cnum_ov)
                        gidqi_clat_ov.append(gidqi_clevel_ov)
                        gidqi_clat_ov.append(gidqi_cnum_ov)
                        last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
                    else:
                        Tds_clat_ov.append(Tds_clevel_ov+Tds_cnum_ov)
                        addp_clat_ov.append(addp_clevel_ov+addp_cnum_ov)
                        dWp_clat_ov.append(dWp_clevel_ov+dWp_cnum_ov)
                        gvdqv_clat_ov.append(gvdqv_clevel_ov+gvdqv_cnum_ov)
                        gldql_clat_ov.append(gldql_clevel_ov+gldql_cnum_ov)
                        gidqi_clat_ov.append(gidqi_clevel_ov+gidqi_cnum_ov)
                        last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
    #Calculate MAFALDA-derived energetic quantities as average values over all eyewall levels of the isentropic streamfunction.
    Tds_ov=np.nanmean(Tds_clat_ov) #Wmax for eyewall circulation
    addp_ov=np.nanmean(addp_clat_ov) #W for eyewall circulation
    dWp_ov=np.nanmean(dWp_clat_ov) #Wp for eyewall circulation
    dWKE_clat_arr_ov=np.asarray(addp_clat_ov)-np.asarray(dWp_clat_ov) #WKE for the eyewall circulation at all corresponding levels of the isentropic streamfuntion
    dWKE_clat_ov=dWKE_clat_arr_ov.tolist()
    dWKE_ov=np.nanmean(dWKE_clat_ov) #WKE for eyewall circulation
    gvdqv_ov=np.nanmean(gvdqv_clat_ov) #Contribution to Delta(G) from water vapor for eyewall circulation
    gldql_ov=np.nanmean(gldql_clat_ov) #Contribution to Delta(G) from liquid water for eyewall circulation
    gidqi_ov=np.nanmean(gidqi_clat_ov) #Contribution to Delta(G) from solid water for eyewall circulation

    #Record the value of the isentropic streamfunction level corresponding to each eyewall trajectory
    levels2_ov=[]
    for cnum in overturning_cnums: 
        levels2_ov.append(levels2[cnum])

    dg_clat_ov=np.asarray(gvdqv_clat_ov)+np.asarray(gidqi_clat_ov)+np.asarray(gldql_clat_ov) #Gibbs penalty Delta(G) for the eyewall circulation at all corresponding levels of the isentropic streamfuntion
    dg_ov=np.nanmean(dg_clat_ov) #Gibbs penalty Delta(G) for eyewall circulation

    #Now, we check that the MAFALDA equalty Wmax=W+Delta(G) holds to within 5%
    test_equality_ov=(addp_ov-dg_ov)/Tds_ov #Wmax/(W+Delta(G)) based on the average values over all isentropic streamfunction eyewall levels
    if (test_equality_ov<1.05) and (test_equality_ov>0.95): #If the equality holds to within 5%
        print("MAFALDA equality holds for the eyewall circulation!")
        print(test_equality_ov)
    else: #If the equality does not hold to within 5%
        if (test_equality_ov<1.1) and (test_equality_ov>0.9): #If the equality holds to within 10%
            print("WARNING- MAFALDA equality holds to within only 10% for the eyewall circulation")
            print(test_equality_ov)
        else:
            if len(overturning_cnums)==0: #If no overturning trajectories exist, then test_equality_ov=nan
                print("WARNING- No eyewall trajectories exist for this time period")
            else:
                print("ERROR!!!- MAFALDA equality does not hold for the eyewall circulation!")
                print(test_equality_ov)          

    #Calculate the heat input and output, and their associated temperatures for the eyewall circulation
    Qin_clat_ov=[] #Heat input Qin at all isentropic streamfunction eyewall levels
    Qout_clat_ov=[] #Heat output Qout at all isentropic streamfunction eyewall levels
    Tin_clat_ov=[] #Temperature of heat input Tin at all isentropic streamfunction eyewall levels
    Tout_clat_ov=[] #Temperature of heat output Tout at all isentropic streamfunction eyewall levels 
    Qin_Tin_clat_ov=[] #Qin/Tin at all isentropic streamfunction eyewall levels 
    Qout_Tout_clat_ov=[] #Qout/Tout at all isentropic streamfunction eyewall levels 
    for cnum in overturning_cnums: #Loop through all eyewall trajectories
        if len(interpolated_t[cnum])>2: 
            [Qin_cnum_ov, Qin_Tin_cnum_ov]=getQin(interpolated_t[cnum], interpolated_ent[cnum], interpolated_gv[cnum], interpolated_qv[cnum], interpolated_gl[cnum], interpolated_ql[cnum], interpolated_gi[cnum], interpolated_qi[cnum])
            [Qout_cnum_ov, Qout_Tout_cnum_ov]=getQout(interpolated_t[cnum], interpolated_ent[cnum], interpolated_gv[cnum], interpolated_qv[cnum], interpolated_gl[cnum], interpolated_ql[cnum], interpolated_gi[cnum], interpolated_qi[cnum])
            if len(overturning_cnums)==1: #If only one eyewall trajectory exists, proceed as follows:
                #Set the value of each variable at the current and only eyewall level of the isentropic streamfunction to the values that we just calculated for the current trajectory
                Qin_clat_ov=Qin_cnum_ov
                Qout_clat_ov=Qout_cnum_ov
                Qin_Tin_clat_ov=Qin_Tin_cnum_ov
                Qout_Tout_clat_ov=Qout_Tout_cnum_ov 
                #Calculate Tin and Tout for the single eyewall trajectory
                Tin_clat_ov=Qin_cnum_ov/Qin_Tin_cnum_ov
                if np.abs(Qin_Tin_cnum_ov)<10**(-15): #Don't want to divide by zero!
                    Tin_clat_ov=0
                Tout_clat_ov=Qout_cnum_ov/Qout_Tout_cnum_ov
                if np.abs(Qout_Tout_cnum_ov)<10**(-15):
                    Tout_clat_ov=0                
            else: #If more than one eyewall trajectory exists, proceed as follows:
                if (cnum!=overturning_cnums[0])&(cnum!=overturning_cnums[-1]): #If we are not at the first eyewall level's first trajectory and not at the last eyewall level's last trajectory
                    if levels2[cnum]!=levels2[last_cnum]: #If we have just changed levels
                        Tin_clevel_ov=Qin_clevel_ov/Qin_Tin_clevel_ov 
                        if np.abs(Qin_Tin_clevel_ov)<10**(-15): 
                            Tin_clevel_ov=0
                        Tout_clevel_ov=Qout_clevel_ov/Qout_Tout_clevel_ov
                        if np.abs(Qout_Tout_clevel_ov)<10**(-15):
                            Tout_clevel_ov=0                   
                        Qin_clat_ov.append(Qin_clevel_ov)
                        Qin_Tin_clat_ov.append(Qin_Tin_clevel_ov)
                        Qin_clevel_ov=Qin_cnum_ov
                        Qin_Tin_clevel_ov=Qin_Tin_cnum_ov
                        Tin_clat_ov.append(Tin_clevel_ov)                 
                        Qout_clat_ov.append(Qout_clevel_ov)
                        Qout_Tout_clat_ov.append(Qout_Tout_clevel_ov)
                        Qout_clevel_ov=Qout_cnum_ov  
                        Qout_Tout_clevel_ov=Qout_Tout_cnum_ov                       
                        Tout_clat_ov.append(Tout_clevel_ov)                          
                        last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
                    else:
                        Qin_clevel_ov+=Qin_cnum_ov
                        Qin_Tin_clevel_ov+=Qin_Tin_cnum_ov
                        Qout_clevel_ov+=Qout_cnum_ov
                        Qout_Tout_clevel_ov+=Qout_Tout_cnum_ov                        
                        last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
                elif (cnum==overturning_cnums[0]): #If we are at the first eyewall level of the isentropic streamfunction, initialize the variables Qin_clevel_ov, etc.
                    Qin_clevel_ov=Qin_cnum_ov
                    Qin_Tin_clevel_ov=Qin_Tin_cnum_ov
                    Qout_clevel_ov=Qout_cnum_ov
                    Qout_Tout_clevel_ov=Qout_Tout_cnum_ov                    
                    last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
                elif (cnum==overturning_cnums[-1]): #If we are at the last eyewall level's last trajectory
                    if levels2[cnum]!=levels2[last_cnum]: #If the last trajectory corresponds to a new level
                        Tin_clevel_ov=Qin_clevel_ov/Qin_Tin_clevel_ov 
                        if np.abs(Qin_Tin_clevel_ov)<10**(-15): 
                            Tin_clevel_ov=0
                        Tout_clevel_ov=Qout_clevel_ov/Qout_Tout_clevel_ov                       
                        if np.abs(Qout_Tout_clevel_ov)<10**(-15):
                            Tout_clevel_ov=0                    
                        Qin_clat_ov.append(Qin_clevel_ov)
                        Qin_Tin_clat_ov.append(Qin_Tin_clevel_ov)
                        Qin_clat_ov.append(Qin_cnum_ov)
                        Qin_Tin_clat_ov.append(Qin_Tin_cnum_ov)
                        Qout_clat_ov.append(Qout_clevel_ov)
                        Qout_Tout_clat_ov.append(Qout_Tout_clevel_ov)
                        Qout_clat_ov.append(Qout_cnum_ov) 
                        Qout_Tout_clat_ov.append(Qout_Tout_cnum_ov)
                        Tin_clat_ov.append(Tin_clevel_ov)
                        Tout_clat_ov.append(Tout_clevel_ov) 
                        Tin_clevel_ov=Qin_cnum_ov/Qin_Tin_cnum_ov 
                        if np.abs(Qin_Tin_cnum_ov)<10**(-15): 
                            Tin_clevel_ov=0                        
                        Tout_clevel_ov=Qout_cnum_ov/Qout_Tout_cnum_ov
                        if np.abs(Qout_Tout_cnum_ov)<10**(-15):
                            Tout_clevel_ov=0                           
                        Tin_clat_ov.append(Tin_clevel_ov)
                        Tout_clat_ov.append(Tout_clevel_ov)                         
                        last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
                    else:
                        Tin_clevel_ov=(Qin_clevel_ov+Qin_cnum_ov)/(Qin_Tin_clevel_ov+Qin_Tin_cnum_ov) #When the last level finishes, calculate Tin and Tout for that level!
                        if np.abs(Qin_Tin_clevel_ov+Qin_Tin_cnum_ov)<10**(-15):
                            Tin_clevel_ov=0
                        Tout_clevel_ov=(Qout_clevel_ov+Qout_cnum_ov)/(Qout_Tout_clevel_ov+Qout_Tout_cnum_ov)
                        if np.abs(Qout_Tout_clevel_ov+Qout_Tout_cnum_ov)<10**(-15):
                            Tout_clevel_ov=0
                        Qin_clevel_ov+=Qin_cnum_ov
                        Qin_Tin_clevel_ov+=Qin_Tin_cnum_ov
                        Qout_clevel_ov+=Qout_cnum_ov
                        Qout_Tout_clevel_ov+=Qout_Tout_cnum_ov
                        Qin_clat_ov.append(Qin_clevel_ov)
                        Qin_Tin_clat_ov.append(Qin_Tin_clevel_ov)
                        Tin_clat_ov.append(Tin_clevel_ov)
                        Qout_clat_ov.append(Qout_clevel_ov)
                        Qout_Tout_clat_ov.append(Qout_Tout_clevel_ov)
                        Tout_clat_ov.append(Tout_clevel_ov)                           
                        last_cnum=cnum #Helps track the value of the previous eyewall level of the isentropic streamfunction
    #Calculate Qin, Qout, Qin/Tin, and Qout/Tout as average values over all eyewall levels of the isentropic streamfunction.
    Qin_ov=np.nanmean(Qin_clat_ov) #Heat input for eyewall circulation
    Qin_Tin_ov=np.nanmean(Qin_Tin_clat_ov) #Qin/Tin for eyewall circulation
    Qout_ov=np.nanmean(Qout_clat_ov) #Heat output for eyewall circulation
    Qout_Tout_ov=np.nanmean(Qout_Tout_clat_ov) #Qout/Tout for eyewall circulation
    #Calculate Tin, Tout, etc.
    Tin_ov=Qin_ov/Qin_Tin_ov #Temperature of heat input for eyewall circulation
    Tout_ov=Qout_ov/Qout_Tout_ov #Temperature of heat output for eyewall circulation
    eta_c_ov=(Tin_ov-Tout_ov)/Tin_ov #Carnot efficiency for eyewall circulation
    mech_eff_ov=np.asarray(dWKE_clat_ov)/np.asarray(Qin_clat_ov) #Mechanical efficiency at all isentropic streamfunction eyewall levels
    
    #Repeat the above procedure for the rainband circulation only
    
    Tds_clat_rb=[] #Wmax for the rainband circulation at all corresponding levels of the isentropic streamfunction
    addp_clat_rb=[] #W for the rainband circulation at all corresponding levels of the isentropic streamfunction
    dWp_clat_rb=[] #Wp for the rainband circulation at all corresponding levels of the isentropic streamfunction
    gvdqv_clat_rb=[] #Contribution to Delta(G) from water vapor for the rainband circulation at all corresponding levels of the isentropic streamfunction
    gldql_clat_rb=[] #Contribution to Delta(G) from liquid water for the rainband circulation at all corresponding levels of the isentropic streamfunction
    gidqi_clat_rb=[] #Contribution to Delta(G) from solid water for the rainband circulation at all corresponding levels of the isentropic streamfunction
    for cnum in rainband_cnums: #Loop through all rainband trajectories
        if len(interpolated_t[cnum])>2: 
            [Tds_cnum_rb, addp_cnum_rb, dWp_cnum_rb, gvdqv_cnum_rb, gldql_cnum_rb, gidqi_cnum_rb]=MAFALDA(interpolated_t[cnum], interpolated_ent[cnum], interpolated_ad[cnum], interpolated_p[cnum], interpolated_WPint[cnum], interpolant_z_arr[cnum], interpolated_gv[cnum], interpolated_qv[cnum], interpolated_gl[cnum], interpolated_ql[cnum], interpolated_gi[cnum], interpolated_qi[cnum])
            if (cnum!=rainband_cnums[0])&(cnum!=rainband_cnums[-1]): #If we are not at the first rainband level's first trajectory and not at the last rainband level's last trajectory
                if levels2[cnum]!=levels2[last_cnum]: #If we have just changed levels
                    Tds_clat_rb.append(Tds_clevel_rb)
                    Tds_clevel_rb=Tds_cnum_rb
                    addp_clat_rb.append(addp_clevel_rb)
                    addp_clevel_rb=addp_cnum_rb
                    dWp_clat_rb.append(dWp_clevel_rb)
                    dWp_clevel_rb=dWp_cnum_rb
                    gvdqv_clat_rb.append(gvdqv_clevel_rb)
                    gvdqv_clevel_rb=gvdqv_cnum_rb
                    gldql_clat_rb.append(gldql_clevel_rb)
                    gldql_clevel_rb=gldql_cnum_rb
                    gidqi_clat_rb.append(gidqi_clevel_rb)
                    gidqi_clevel_rb=gidqi_cnum_rb
                    last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
                else:
                    Tds_clevel_rb+=Tds_cnum_rb
                    addp_clevel_rb+=addp_cnum_rb
                    dWp_clevel_rb+=dWp_cnum_rb
                    gvdqv_clevel_rb+=gvdqv_cnum_rb
                    gldql_clevel_rb+=gldql_cnum_rb
                    gidqi_clevel_rb+=gidqi_cnum_rb
                    last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
            elif (cnum==rainband_cnums[0]):#If we are at the first rainband level of the isentropic streamfunction, initialize the variables Tds_clevel_rb, etc.
                Tds_clevel_rb=Tds_cnum_rb
                addp_clevel_rb=addp_cnum_rb
                dWp_clevel_rb=dWp_cnum_rb
                gvdqv_clevel_rb=gvdqv_cnum_rb
                gldql_clevel_rb=gldql_cnum_rb
                gidqi_clevel_rb=gidqi_cnum_rb
                last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
            elif (cnum==rainband_cnums[-1]): #If we are at the last rainband level's last trajectory
                if levels2[cnum]!=levels2[last_cnum]: #If the last trajectory corresponds to a new level
                    Tds_clat_rb.append(Tds_clevel_rb)
                    Tds_clat_rb.append(Tds_cnum_rb)
                    addp_clat_rb.append(addp_clevel_rb)
                    addp_clat_rb.append(addp_cnum_rb)
                    dWp_clat_rb.append(dWp_clevel_rb)
                    dWp_clat_rb.append(dWp_cnum_rb)
                    gvdqv_clat_rb.append(gvdqv_clevel_rb)
                    gvdqv_clat_rb.append(gvdqv_cnum_rb)
                    gldql_clat_rb.append(gldql_clevel_rb)
                    gldql_clat_rb.append(gldql_cnum_rb)
                    gidqi_clat_rb.append(gidqi_clevel_rb)
                    gidqi_clat_rb.append(gidqi_cnum_rb)
                    last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
                else:
                    Tds_clat_rb.append(Tds_clevel_rb+Tds_cnum_rb)
                    addp_clat_rb.append(addp_clevel_rb+addp_cnum_rb)
                    dWp_clat_rb.append(dWp_clevel_rb+dWp_cnum_rb)
                    gvdqv_clat_rb.append(gvdqv_clevel_rb+gvdqv_cnum_rb)
                    gldql_clat_rb.append(gldql_clevel_rb+gldql_cnum_rb)
                    gidqi_clat_rb.append(gidqi_clevel_rb+gidqi_cnum_rb)
                    last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
    #Calculate MAFALDA-derived energetic quantities as average values over all rainband levels of the isentropic streamfunction.
    Tds_rb=np.nanmean(Tds_clat_rb) #Wmax for the rainband circulation
    addp_rb=np.nanmean(addp_clat_rb) #W for the rainband circulation
    dWp_rb=np.nanmean(dWp_clat_rb) #Wp for the rainband circulation
    dWKE_clat_arr_rb=np.asarray(addp_clat_rb)-np.asarray(dWp_clat_rb) #WKE for the rainband circulation at all corresponding levels of the isentropic streamfuntion
    dWKE_clat_rb=dWKE_clat_arr_rb.tolist()
    dWKE_rb=np.nanmean(dWKE_clat_rb) #WKE for the rainband circulation
    gvdqv_rb=np.nanmean(gvdqv_clat_rb) #Contribution to Delta(G) from water vapor for the rainband circulation
    gldql_rb=np.nanmean(gldql_clat_rb) #Contribution to Delta(G) from liquid water for the rainband circulation
    gidqi_rb=np.nanmean(gidqi_clat_rb) #Contribution to Delta(G) from solid water for the rainband circulation

    #Record the value of the isentropic streamfunction level corresponding to each rainband trajectory
    levels2_rb=[]
    for cnum in rainband_cnums: 
        levels2_rb.append(levels2[cnum])

    dg_clat_rb=np.asarray(gvdqv_clat_rb)+np.asarray(gidqi_clat_rb)+np.asarray(gldql_clat_rb) #Gibbs penalty Delta(G) for the rainband circulation at all corresponding levels of the isentropic streamfuntion
    dg_rb=np.nanmean(dg_clat_rb) #Gibbs penalty Delta(G) for the rainband circulation

    #Now, we check that the MAFALDA equalty Wmax=W+Delta(G) holds to within 5%
    test_equality_rb=(addp_rb-dg_rb)/Tds_rb #Wmax/(W+Delta(G)) based on the average values over all isentropic streamfunction rainband levels
    if (test_equality_rb<1.05) and (test_equality_rb>0.95): #If the equality holds to within 5%
        print("MAFALDA equality holds for the rainband circulation!")
        print(test_equality_rb)
    else: #If the equality does not hold to within 5%
        if (test_equality_rb<1.1) and (test_equality_rb>0.9): #If the equality holds to within 10%
            print("WARNING- MAFALDA equality holds to within only 10% for the rainband circulation")
            print(test_equality_rb)
        else:
            print("ERROR!!!- MAFALDA equality does not hold for the rainband circulation!")
            print(test_equality_rb)              
    
    #Calculate the heat input and output, and their associated temperatures for the rainband circulation
    Qin_clat_rb=[] #Heat input Qin at all isentropic streamfunction rainband levels
    Qout_clat_rb=[] #Heat output Qout at all isentropic streamfunction rainband levels
    Tin_clat_rb=[] #Temperature of heat input Tin at all isentropic streamfunction rainband levels
    Tout_clat_rb=[] #Temperature of heat output Tout at all isentropic streamfunction rainband levels 
    Qin_Tin_clat_rb=[] #Qin/Tin at all isentropic streamfunction rainband levels
    Qout_Tout_clat_rb=[] #Qout/Tout at all isentropic streamfunction rainband levels
    for cnum in rainband_cnums: #Loop through all rainband trajectories
        if len(interpolated_t[cnum])>2: 
            [Qin_cnum_rb, Qin_Tin_cnum_rb]=getQin(interpolated_t[cnum], interpolated_ent[cnum], interpolated_gv[cnum], interpolated_qv[cnum], interpolated_gl[cnum], interpolated_ql[cnum], interpolated_gi[cnum], interpolated_qi[cnum])
            [Qout_cnum_rb, Qout_Tout_cnum_rb]=getQout(interpolated_t[cnum], interpolated_ent[cnum], interpolated_gv[cnum], interpolated_qv[cnum], interpolated_gl[cnum], interpolated_ql[cnum], interpolated_gi[cnum], interpolated_qi[cnum])
            if (cnum!=rainband_cnums[0])&(cnum!=rainband_cnums[-1]): #If we are not at the first rainband level's first trajectory and not at the last rainband level's last trajectory
                if levels2[cnum]!=levels2[last_cnum]: #If we have just changed levels
                    Tin_clevel_rb=Qin_clevel_rb/Qin_Tin_clevel_rb 
                    if np.abs(Qin_Tin_clevel_rb)<10**(-15): 
                        Tin_clevel_rb=0
                    Tout_clevel_rb=Qout_clevel_rb/Qout_Tout_clevel_rb
                    if np.abs(Qout_Tout_clevel_rb)<10**(-15):
                        Tout_clevel_rb=0                      
                    Qin_clat_rb.append(Qin_clevel_rb)
                    Qin_Tin_clat_rb.append(Qin_Tin_clevel_rb)
                    Qin_clevel_rb=Qin_cnum_rb
                    Qin_Tin_clevel_rb=Qin_Tin_cnum_rb
                    Tin_clat_rb.append(Tin_clevel_rb)                 
                    Qout_clat_rb.append(Qout_clevel_rb)
                    Qout_Tout_clat_rb.append(Qout_Tout_clevel_rb)
                    Qout_clevel_rb=Qout_cnum_rb  
                    Qout_Tout_clevel_rb=Qout_Tout_cnum_rb                       
                    Tout_clat_rb.append(Tout_clevel_rb)                    
                    last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
                else:
                    Qin_clevel_rb+=Qin_cnum_rb
                    Qin_Tin_clevel_rb+=Qin_Tin_cnum_rb
                    Qout_clevel_rb+=Qout_cnum_rb
                    Qout_Tout_clevel_rb+=Qout_Tout_cnum_rb                     
                    last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
            elif (cnum==rainband_cnums[0]): #If we are at the first rainband level of the isentropic streamfunction, initialize the variables Qin_clevel_rb, etc.
                Qin_clevel_rb=Qin_cnum_rb
                Qin_Tin_clevel_rb=Qin_Tin_cnum_rb
                Qout_clevel_rb=Qout_cnum_rb
                Qout_Tout_clevel_rb=Qout_Tout_cnum_rb                   
                last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
            elif (cnum==rainband_cnums[-1]): #If we are at the last rainband level's last trajectory
                if levels2[cnum]!=levels2[last_cnum]: #If the last trajectory corresponds to a new level
                    Tin_clevel_rb=Qin_clevel_rb/Qin_Tin_clevel_rb 
                    if np.abs(Qin_Tin_clevel_rb)<10**(-15): 
                        Tin_clevel_rb=0
                    Tout_clevel_rb=Qout_clevel_rb/Qout_Tout_clevel_rb
                    if np.abs(Qout_Tout_clevel_rb)<10**(-15):
                        Tout_clevel_rb=0                    
                    Qin_clat_rb.append(Qin_clevel_rb)
                    Qin_Tin_clat_rb.append(Qin_Tin_clevel_rb)
                    Qin_clat_rb.append(Qin_cnum_rb)
                    Qin_Tin_clat_rb.append(Qin_Tin_cnum_rb)
                    Qout_clat_rb.append(Qout_clevel_rb)
                    Qout_Tout_clat_rb.append(Qout_Tout_clevel_rb)
                    Qout_clat_rb.append(Qout_cnum_rb)
                    Qout_Tout_clat_rb.append(Qout_Tout_cnum_rb)
                    Tin_clat_rb.append(Tin_clevel_rb)
                    Tout_clat_rb.append(Tout_clevel_rb) 
                    Tin_clevel_rb=Qin_cnum_rb/Qin_Tin_cnum_rb 
                    if np.abs(Qin_Tin_cnum_rb)<10**(-15): 
                        Tin_clevel_rb=0                        
                    Tout_clevel_rb=Qout_cnum_rb/Qout_Tout_cnum_rb
                    if np.abs(Qout_Tout_cnum_rb)<10**(-15):
                        Tout_clevel_rb=0    
                    Tin_clat_rb.append(Tin_clevel_rb)
                    Tout_clat_rb.append(Tout_clevel_rb)                      
                    last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
                else:
                    Tin_clevel_rb=(Qin_clevel_rb+Qin_cnum_rb)/(Qin_Tin_clevel_rb+Qin_Tin_cnum_rb) #When the last level finishes, calculate Tin and Tout for that level! 
                    if np.abs(Qin_Tin_clevel_rb+Qin_Tin_cnum_rb)<10**(-15):
                        Tin_clevel_rb=0
                    Tout_clevel_rb=(Qout_clevel_rb+Qout_cnum_rb)/(Qout_Tout_clevel_rb+Qout_Tout_cnum_rb)
                    if np.abs(Qout_Tout_clevel_rb+Qout_Tout_cnum_rb)<10**(-15):
                        Tout_clevel_rb=0
                    Qin_clevel_rb+=Qin_cnum_rb
                    Qin_Tin_clevel_rb+=Qin_Tin_cnum_rb
                    Qout_clevel_rb+=Qout_cnum_rb
                    Qout_Tout_clevel_rb+=Qout_Tout_cnum_rb
                    Qin_clat_rb.append(Qin_clevel_rb)
                    Qin_Tin_clat_rb.append(Qin_Tin_clevel_rb)
                    Tin_clat_rb.append(Tin_clevel_rb)
                    Qout_clat_rb.append(Qout_clevel_rb)
                    Qout_Tout_clat_rb.append(Qout_Tout_clevel_rb)
                    Tout_clat_rb.append(Tout_clevel_rb)                     
                    last_cnum=cnum #Helps track the value of the previous rainband level of the isentropic streamfunction
    #Calculate Qin, Qout, Qin/Tin, and Qout/Tout as average values over all rainband levels of the isentropic streamfunction.
    Qin_rb=np.nanmean(Qin_clat_rb) #Heat input for rainband circulation
    Qin_Tin_rb=np.nanmean(Qin_Tin_clat_rb) #Qin/Tin for rainband circulation
    Qout_rb=np.nanmean(Qout_clat_rb) #Heat output for rainband circulation
    Qout_Tout_rb=np.nanmean(Qout_Tout_clat_rb) #Qout/Tout for rainband circulation
    #Calculate Tin, Tout, etc.
    Tin_rb=Qin_rb/Qin_Tin_rb #Temperature of heat input for rainband circulation
    Tout_rb=Qout_rb/Qout_Tout_rb #Temperature of heat output for rainband circulation
    eta_c_rb=(Tin_rb-Tout_rb)/Tin_rb #Carnot efficiency for rainband circulation     
    mech_eff_rb=np.asarray(dWKE_clat_rb)/np.asarray(Qin_clat_rb) #Mechanical efficiency at all isentropic streamfunction rainband levels
    
    #Calculate mechanical efficiency quantities as average values over all trajectories corresponding to various subsets of levels of the isentropic streamfunction
    eta_mech=dWKE/Qin #Mechanical efficiency for all levels of the isentroic streamfunction
    eta_mech_ov=dWKE_ov/Qin_ov #Mechanical efficiency for the eyewall circulation   
    eta_mech_rb=dWKE_rb/Qin_rb #Mechanical efficiency for the rainband circulation     


    #Calculate the moisture penalty, Wmoist=Wp+Delta(G), based on the averages of Wp and Delta(G) over all trajectories corresponding to various subsets of levels of the isentropic streamfunction
    moisture=dWp-dg #Wmoist for all levels of the isentroic streamfunction 
    moisture_ov=dWp_ov-dg_ov #Wmoist for the eyewall circulation
    moisture_rb=dWp_rb-dg_rb #Wmoist for the rainband circulation
    

    #Save variables for use in making plots and deriving trends with SST in MAFALDA_plots.py
    filename="Qin_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, Qin=Qin, Qin_2=Qin_2)
    filename="Tds_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, Tds=Tds)
    filename="addp_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, addp=addp)
    filename="dWp_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, dWp=dWp, dWp_2=dWp_2)
    filename="dWKE_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, dWKE=dWKE, dWKE_2=dWKE_2)
    filename="dg_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, dg=dg, dg_2=dg_2)    
    filename="moisture_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, moisture=moisture)


    filename="Qin_ov_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, Qin_ov=Qin_ov)
    filename="Tds_ov_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, Tds_ov=Tds_ov)
    filename="addp_ov_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, addp_ov=addp_ov)
    filename="dWp_ov_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, dWp_ov=dWp_ov)
    filename="dWKE_ov_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, dWKE_ov=dWKE_ov)
    filename="dg_ov_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, dg_ov=dg_ov)    
    filename="moisture_ov_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, moisture_ov=moisture_ov)
        

    filename="Qin_rb_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, Qin_rb=Qin_rb)
    filename="Tds_rb_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, Tds_rb=Tds_rb)
    filename="addp_rb_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, addp_rb=addp_rb)
    filename="dWp_rb_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, dWp_rb=dWp_rb)
    filename="dWKE_rb_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, dWKE_rb=dWKE_rb)
    filename="dg_rb_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, dg_rb=dg_rb)    
    filename="moisture_rb_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, moisture_rb=moisture_rb)

    filename="eta_mech_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, eta_mech=eta_mech)    
    filename="eta_mech_ov_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, eta_mech_ov=eta_mech_ov)       
    filename="eta_mech_rb_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, eta_mech_rb=eta_mech_rb)    

    filename="KE_pm_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, KE_pm=KE_pm)
    
    filename="IKE_" +np.str(SST)+"_"+"_axisymm_Rp.npz" 
    np.savez(filename, IKE=IKE) 
    
    filename="Heat_flux_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, totflux=totflux, shflux=shflux, lhflux=lhflux)  
    
    filename="pr_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, pr=pr)      
    
    filename="ov_flag_" +np.str(SST)+"_Rp.npz" #Save a "flag" that denotes whether or not no eyewall trajectories were
                                               #found for the current 2-day period. This flag is used by MAFALDA_plots.py
    if len(overturning_cnums)==0:
        print("No eyewall trajectories")
        ov_flag=1
        np.savez(filename, ov_flag=ov_flag)  
    else:
        ov_flag=0
        np.savez(filename, ov_flag=ov_flag) 
        
    filename="eta_c_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, eta_c=eta_c, Tin=Tin, Tout=Tout, Qout=Qout)     
    filename="eta_c_ov_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, eta_c_ov=eta_c_ov, Tin_ov=Tin_ov, Tout_ov=Tout_ov, Qout_ov=Qout_ov)   
    filename="eta_c_rb_" +np.str(SST)+"_axisymm_Rp.npz" 
    np.savez(filename, eta_c_rb=eta_c_rb, Tin_rb=Tin_rb, Tout_rb=Tout_rb, Qout_rb=Qout_rb)  
    

The following function performs the "isentropic average" of an input variable, file_in, and returns the time-average of this isentropically-averaged quantity. 

The inputs are:
1. file_in, the variable on which we wish to perform the isentropic average
2. th_e, the equivalent potential temperature (K) as a function of height, radius, and time. Its dimensions must match those of file_in
3. Three parameters that set the theta_e "bins" for the isentropic integral: th_min, the minimum value of theta_e for the bins, th_max, the maximum value of theta_e for the bins, and delt, the half-width of the theta_e bins.
4. x, the radial gridpoints (m)
5. xlen, the length of x
6. zlen, the length of z, which contains the height gridpoints
7. perArea, which contains the numerical equivalent of the horizontal "area" in the domain. We divide the result of the isentropic integral by this quantity to obtain the isentropic average. Given how the following code is structured. perArea=np.sum(x) is appropriate since factors of 2np.pi and dx (assumed constant in this code!) are left out of both the numerator and the denominator (and hence their exclusion cancels out). If instead perArea=2np.pi np.sum(x dx), the code below would need to be altered to include factors of 2 np.pi and dx within the isentropic integrand
8. tstart, the timestep corresponding to the beginning of the current time period
9. tfinal, the timestep immediately after the end of the current time period

The output is:
1. file_out, the isentropic- and time-average value of file_in.

In [ ]:
def isentropic_integral(file_in, th_e, th_min, th_max, delt, x, xlen, zlen, perArea, tstart, tfinal): 
    number=(th_max-th_min)/(2*delt) #Number of theta_e bins
    bins=np.arange(th_min-delt, th_max+delt, delt*2) #Define theta_e bins based on the parameters th_min, th_max, and delt

    #Perform the isentropic integral of the input, f, to get <f>(z, theta_e, t), and store in temp2. We then divide by perArea to get the isentropic-average of file_in
    #The following code loops through theta_e bins defined above and searches for the points (r, z, t) with theta_e values that fall inside these bins
    #Once these points (r, z, t) are obtained, the code performs the isentropic horizontal integral for each z value. The result of this is stored in temp2b.
    #After this, the vector temp2b (which has dimensions zx1xt) is added to the array temp2 as a column. temp2 has dimensions of zx(number of theta_e bins)xt
    for b in bins: #"For a given theta e bin, do the following"
        if b != bins[int(number)]: #Don't deal with last bin since it is redundant given how I write the next line- would be like counting the last bin twice
            [zindex, xindex, tindex]=np.where((th_e>b) & (th_e<=b+1)) #Get indices of all points (r, z, t) at which theta_e values fall within the theta_e bin of interest. 
            #In what follows, a single such point (r, z, t) would be given by (x[xindex[i]], z[zindex[i]], t[tindex[i]]), where i is some index between 0 and the length of xindex.
            temp2b=np.zeros((zlen, 1, (tfinal-tstart))) #Initialize temp2b, which will hold the result of the isentropic integral for given values of z, t, and a given theta e bin. Dimensions are zx1xt
            #Now that we have found the points (r, z, t) of interest for a given theta_e bin, we calculate the isentropic integral wrt r for each z value
            for i in np.unique(zindex): #"Do the following for a given z value in the set of points denoted by zindex, xindex, and tindex"
                for m in np.unique(tindex[zindex==i]): #"Within the subset of t values corresponding to the current z value, do the following"
                    integrand=[] 
                    indices=np.where((zindex==i)&(tindex==m))[0] #For the chosen z and t values, z' and t', find all points (r, z=z', t=t')
                    #For the chosen z and t values, z' and t', calculate the integrand at all points (r, z=z', t=t'): f(r, z=z', t=t')*r 
                    for j in indices: 
                        integrand.append(file_in[i, xindex[j], m]*x[xindex[j]]) #Calculate the integrand, f(r, z=z', t=t')*r , at all points (r, z=z', t=t') 
                    temp2b[i, :, m]=np.sum(integrand, axis=0) #Perform the isentropic integral: <f>(theta_e bin, z=z', t=t')=integral(f(r, z=z', t=t')*r dr, limits: (0, L_outer))
            #temp2b contains the result of the isentropic integral for all values of t and z corresponding to the current theta_e bin.
            #Now, we add temp2b to temp2 in the position corresponding to the current theta_e bin.            
            if b==bins[0]: #For the first bin, we need to handle things as a special case to initialize temp2
                    temp2=temp2b #Initialize temp2, which contains the result of the isentropic integral at all values of z, t, and theta_e 
            else: 
                temp2=np.concatenate((temp2, temp2b), axis=1) #Concatenate temp2b along the theta_e dimension of temp2
    temp2=temp2/perArea #Divide temp2 by the horizontal area of the domain to obtain the isentropic-average value of file_in, <f>(z, theta_e, t) 
    
    #Perform the time integral of the isentropic-average of file_in, temp2
    taverage=np.sum(temp2, axis=2) #Integrate along the time axis. No need to multiply by dt because if we divide by tfinal-tstart (time period in units of # of timestamps) then dt=1 timestamp
    tavg=taverage/(tfinal-tstart) #Divide by tau=tfinal-tstart
    file_out=tavg 
    return file_out #Return the isentropic- and time-average of file_in 

The following code calculates the Eulerian streamfunction of the TC during the time period of interest given input axisymmetric data (data that is a function of radius and height only)

The inputs are:
1. radwind, the time-mean radial wind speed (m/s)
2. wwind, the time-mean vertical wind speed (m/s)
3. rhofield, the time-mean density (kg/m^3). 
4. rfield, the radial gridpoints (m). This must have the same shape as radwind, wwind, and rhofield.
5. drfield, the radial grid spacing (m). This must have the same shape as radwind, wwind, and rhofield.
6. zfield, the vertical gridpoints (m). This must have the same shape as radwind, wwind, and rhofield.
7. dzfield, the vertical grid spacing (m). This must have the same shape as radwind, wwind, and rhofield.

The output is:
1. The Eulerian streamfunction as a function of r and z.

In [ ]:
def streamfun(radwind,wwind,rhofield,rfield,drfield,zfield,dzfield):
    Psi_r = -np.cumsum(rfield*rhofield*wwind*drfield,axis=1) #Radial integral
    Psi_z = np.cumsum(rfield*rhofield*radwind*dzfield,axis=0) #Vertical integral
    streamfield = 0.5*(Psi_r + Psi_z) #Calculate Eulerian streamfunction
    return streamfield

The following code for calculating the saturation vapor pressure was written by Bjorn Stevens and can be found at https://github.com/bjorn-stevens/Thermodynamics/blob/master/saturation-water-vapor.ipynb

In [ ]:
def eslf(T, formula="wagner-pruss"):
    #Returns the saturation vapour pressure [Pa] over liquid given the temperature.  
    #Temperatures can be in Celcius or Kelvin.
    #Formulas supported are
    #  - Goff-Gratch (1994 Smithsonian Tables)
    #  - Sonntag (1994) 
    #  - Flatau
    #  - Magnus Tetens (MT)
    #  - Romps (2017)
    #  - Mpurhpy-Koop
    #  - Bolton
    #  - Wagner and Pruss (WP, 2002) is the default
      

    x = T

    if formula == "flatau":
        if (np.min(x) > 100): x = x-273.16
        np.maximum(x,-80.)
        c_es= np.asarray([0.6105851e+03, 0.4440316e+02, 0.1430341e+01, 0.2641412e-01,
                           0.2995057e-03,0.2031998e-05,0.6936113e-08,0.2564861e-11,-0.3704404e-13])
        es = np.polyval(c_es[::-1],x)
    elif formula == "bolton":
        if (np.min(x) > 100): x = x-273.15
        es = 611.2*np.exp((17.67*x)/(243.5+x))
    elif formula == "sonntag":
        xx = -6096.9385/x + 16.635794 - 2.711193e-2*x + 1.673952e-5*x*x + 2.433502 * np.log(x)
        es = 100.*np.exp(xx)
    elif formula =='goff-gratch':
        x1 = 273.16/x
        x2 = 373.16/x
        xl = np.log10(1013.246 ) - 7.90298*(x2 - 1) + 5.02808*np.log10(x2) - 1.3816e-7*(10**(11.344*(1.-1./x2)) - 1.0) + 8.1328e-3 * (10**(-3.49149*(x2-1)) - 1.0)
        es =10**(xl+2) # plus 2 converts from hPa to Pa
    elif formula == 'wagner-pruss':
        vt = 1.-x/TvC
        es = PvC * np.exp(TvC/x * (-7.85951783*vt + 1.84408259*vt**1.5 - 11.7866497*vt**3 + 22.6807411*vt**3.5 - 15.9618719*vt**4 + 1.80122502*vt**7.5))
    elif formula == 'hardy98':
        y  = -2.8365744e+3/(x*x) - 6.028076559e+3/x + 19.54263612 - 2.737830188e-2*x + 1.6261698e-5*x**2 + 7.0229056e-10*x**3 - 1.8680009e-13*x**4 + 2.7150305 * np.log(x)
        es = np.exp(y)
    elif formula == 'romps':
        Rr    = 461.
        cvl_r = 4119
        cvv_r = 1418
        cpv_r = cvv_r + Rr
        es = 611.65 * (x/TvT) **((cpv_r-cvl_r)/Rr) * np.exp((2.37403e6 - (cvv_r-cvl_r)*TvT)*(1/TvT - 1/x)/Rr)
    elif formula == "murphy-koop":
        es = np.exp(54.842763 - 6763.22/x - 4.210*np.log(x) + 0.000367*x + np.tanh(0.0415*(x - 218.8)) * (53.878 - 1331.22/x - 9.44523 * np.log(x) + 0.014025*x))
    elif formula == "standard-analytic":
        c1 = (cpv-cl)/Rv
        c2 = lvT/(Rv*TvT) - c1
        es = PvT * np.exp(c2*(1.-TvT/x)) * (x/TvT)**c1
    else:
        exit("formula not supported")

    es = np.maximum(es,0)
    #if scalar_input:
    #    return np.squeeze(es)
    return es

def esif(T, formula="wagner-pruss"):
    #Returns the saturation vapour pressure [Pa] over ice given the temperature.  
    #Temperatures can be in Celcius or Kelvin.uses the Goff-Gratch (1994 Smithsonian Tables) formula

    x = T

    if formula == "sonntag":
        es = 100 * np.exp(24.7219 - 6024.5282/x + 0.010613868*x - 0.000013198825*x**2 - 0.49382577*np.log(x))
    elif formula == "goff-gratch":
        x1 = 273.16/x
        xi = np.log10(   6.1071) - 9.09718*(x1 - 1) - 3.56654*np.log10(x1) + 0.876793*(1 - 1./x1)
        es = 10**(xi+2)
    elif formula == "wagner-pruss": #(actually wagner et al, 2011)
        a1 = -0.212144006e+2
        a2 =  0.273203819e+2
        a3 = -0.610598130e+1
        b1 =  0.333333333e-2
        b2 =  0.120666667e+1
        b3 =  0.170333333e+1
        theta = T/TvT
        es = PvT * np.exp((a1*theta**b1 + a2 * theta**b2 + a3 * theta**b3)/theta)
    elif formula == "murphy-koop":
        es = np.exp(9.550426 - 5723.265/x + 3.53068 * np.log(x) - 0.00728332*x)
    elif formula == "romps":
        Rr    = 461.
        cvv_r = 1418.
        cvs_r = 1861.
        cpv_r = cvv_r + Rr
        es = 611.65 * (x/TvT) **((cpv_r-cvs_r)/Rr) * np.exp((2.37403e6 + 0.33373e6 - (cvv_r-cvs_r)*TvT)*(1/TvT - 1/x)/Rr)
    elif formula == "standard-analytic":
        c1 = (cpv-ci)/Rv
        c2 = lsT/(Rv*TvT) - c1
        es = PvT * np.exp(c2*(1.-TvT/x)) * (x/TvT)**c1
    else:
        exit("formula not supported")

    es = np.maximum(es,0)
    #if scalar_input:
    #    return np.squeeze(es)
    return es

def esilf(T,formula="wagner-pruss"):
    x = T
    return np.minimum(esif(T,formula),eslf(T,formula))

def Es(T,formula="goff-gratch",state='mxd'): #Laurel edit: put goff-gratch as default formula rather than wagner-pruss


    if (state == 'liq'):
        return eslf(T,formula)
    if (state == 'ice'):
        return esif(T,formula)
    if (state == 'mxd'):
        return esilf(T,formula)

The following code calculates the total heat input, given several input "timeseries" derived from a given MAFALDA trajectory from the isentropic streamfunction.

The inputs are:
1. Temperature (K) "timeseries"
2. Moist entropy (J/kg/K) "timeseries" 
3. Three Gibbs free energy (J/kg) "timeseries" for the Gibbs free energy of water vapor, liquid water, and solid water
4. Three mixing ratio (kg/kg) "timeseries" for the mixing ratios of water vapor, liquid water, and solid water

The ouputs are:
1. The heat input $Q_{in}$ (J/kg) for the MAFALDA trajectory
2. $Q_{in}$/$T_{in}$ for this MAFALDA trajectory, where $T_{in}$ (K) is the temperature corresponding to $Q_{in}$.

In [ ]:
def getQin(t, s, gv, qv, gl, ql, gi, qfr): 
    end=len(s) #Length of the "timeseries" for this MAFALDA trajectory
    #Initialize output variables
    delq_pos=0
    delq_T_pos=0
    for i in range(end-1): #Loop through all points in the "timeseries"  
        #Calculate Tds, gv dqv, gl dql, and gi dqi between the current point and the next point in the "timeseries". 
        #These quantities will be used to calculate Qin
        Tds=-0.5 * (t[i+1] + t[i]) * (s[i+1] - s[i]) 
        gvdqv=-0.5 * (gv[i+1] + gv[i]) * (qv[i+1] - qv[i])
        gldql=-0.5 * (gl[i+1] + gl[i]) * (ql[i+1] - ql[i])
        gidqi=-0.5 * (gi[i+1] + gi[i]) * (qfr[i+1] - qfr[i])
        #Calculate ds, gv/T dqv, gl/T dql, and gi/T dqi between the current point and the next point in the "timeseries".
        ds=-(s[i+1] - s[i])
        gvdqv_T=-(gv[i+1] + gv[i]) * (qv[i+1] - qv[i])/(t[i+1]+t[i])
        gldql_T=-(gl[i+1] + gl[i]) * (ql[i+1] - ql[i])/(t[i+1]+t[i])
        gidqi_T=-(gi[i+1] + gi[i]) * (qfr[i+1] - qfr[i])/(t[i+1]+t[i])
        #If any of these values is nan, set them instead to zero, because if we add "nan" values to any sum, that sum becomes "nan". Setting them to zero ignores these values in the forthcoming sums
        if np.isnan(Tds): 
            Tds=0
        if np.isnan(gvdqv):
            gvdqv=0
        if np.isnan(gldql):
            gldql=0
        if np.isnan(gidqi):
            gidqi=0 
        if np.isnan(ds): 
            ds=0              
        if np.isnan(gvdqv_T):
            gvdqv_T=0
        if np.isnan(gldql_T):
            gldql_T=0
        if np.isnan(gidqi_T):
            gidqi_T=0   
        #Calculate the heating, dq, and heating normalized by temperature, dq/T. 
        #We define dq as in Pauluis and Zhang (2017, JAS) equation (7)
        delq=Tds + gvdqv + gldql + gidqi #Heating calculated between the current and next point in the "timeseries"
        delq_T=ds+ gvdqv_T + gldql_T + gidqi_T #Heating normalized by temperature calculated between the current and next point in the "timeseries"       
        #Following Pauluis and Zhang (2017, JAS) equations (14) and (16), we only add dq and dq/T to the sums that will become Qin and Qin/Tin for 
        #this trajectory if dq>0 and dq/T>0, respectively. Note that dq>0 should imply dq/T>0 because T is positive-definite
        if delq>0:
            delq_pos+=delq #Add to the sum that will become Qin for this trajectory
            if delq_T<0:
                print("ERROR!!!- even if dq>0, dq/T<0!!!")
        if delq_T>0: 
            delq_T_pos+=delq_T #Add to the sum that will become Qin/Tin for this trajectory
            if delq<0:
                print("ERROR!!!- even if dq<0, dq/T>0!!!")
    #The above code obtained dq and dq/T between all points in the "timeseries" except between the last point and first point (recall that the 
    #trajectories are closed loops by construction). Therefore, we must handle this case as well. The code below is as above but specifically considers
    #the first and last points in the "timeseries". Note that if the input "timeseries" are constructed such that the last point is the same as the first 
    #point, the code below will return zero values for "delq" and "delq_T", and so does not alter the values of "delq_pos" or "delq_T_pos". However, 
    #if instead the input "timeseries" has different last and first points, this code can account for that so that it is not a problem.
    Tds=-0.5 * (t[0] + t[-1]) * (s[0] - s[-1])
    gvdqv=-0.5 * (gv[0] + gv[-1]) * (qv[0] - qv[-1])
    gldql=-0.5 * (gl[0] + gl[-1]) * (ql[0] - ql[-1])
    gidqi=-0.5 * (gi[0] + gi[-1]) * (qfr[0] - qfr[-1])  
    ds=-(s[0] - s[-1])
    gvdqv_T=-(gv[0] + gv[-1]) * (qv[0] - qv[-1])/(t[0]+t[-1])
    gldql_T=-(gl[0] + gl[-1]) * (ql[0] - ql[-1])/(t[0]+t[-1])
    gidqi_T=-(gi[0] + gi[-1]) * (qfr[0] - qfr[-1])/(t[0]+t[-1])    
    if np.isnan(Tds): 
        Tds=0    
    if np.isnan(gvdqv):
        gvdqv=0
    if np.isnan(gldql):
        gldql=0
    if np.isnan(gidqi):
        gidqi=0   
    if np.isnan(ds): 
        ds=0    
    if np.isnan(gvdqv_T):
        gvdqv_T=0
    if np.isnan(gldql_T):
        gldql_T=0
    if np.isnan(gidqi_T):
        gidqi_T=0         
    delq=Tds + gvdqv + gldql + gidqi
    delq_T=ds+ gvdqv_T + gldql_T + gidqi_T
    if delq>0:
        delq_pos+=delq
            #if delq_T<0: #OPTIONAL- uncomment this section if the input "timeseries" have their first point different from their last point. However, if the 
            #             #first point is equal to the last point then you should comment out this check since we expect dq, dq/T==0 in these cases.
            #             #Because of numerical errors in Python, in these cases dq and dq/T may not quite be equal to zero but may be small, and 
            #             #potentially opposite-signed. If this occurs then the error message below will be printed but would not reflect an actual problem. 
            #    print("ERROR!!!- even if dq>0, dq/T<0!!!")        
    if delq_T>0: 
        delq_T_pos+=delq_T    
            #if delq<0: #OPTIONAL- uncomment this section if the input "timeseries" have their first point different from their last point. However, if the 
            #             #first point is equal to the last point then you should comment out this check since we expect dq, dq/T==0 in these cases.
            #             #Because of numerical errors in Python, in these cases dq and dq/T may not quite be equal to zero but may be small, and 
            #             #potentially opposite-signed. If this occurs then the error message below will be printed but would not reflect an actual problem. 
            #    print("ERROR!!!- even if dq<0, dq/T>0!!!")        
    return [delq_pos, delq_T_pos] #Return Qin and Qin/Tin for the current trajectory

The following code calculates the total heat output, given several input "timeseries" derived from a given MAFALDA trajectory from the isentropic streamfunction.

The inputs are:
1. Temperature (K) "timeseries"
2. Moist entropy (J/kg/K) "timeseries" 
3. Three Gibbs free energy (J/kg) "timeseries" for the Gibbs free energy of water vapor, liquid water, and solid water
4. Three mixing ratio (kg/kg) "timeseries" for the mixing ratios of water vapor, liquid water, and solid water

The ouputs are:
1. The heat output $Q_{out}$ (J/kg) for the MAFALDA trajectory
2. $Q_{out}$/$T_{out}$ for this MAFALDA trajectory, where $T_{out}$ (K) is the temperature corresponding to $Q_{out}$.

In [ ]:
def getQout(t, s, gv, qv, gl, ql, gi, qfr): 
    end=len(s) #Length of the "timeseries" for this MAFALDA trajectory
    #Initialize output variables
    delq_neg=0
    delq_T_neg=0
    for i in range(end-1): #Loop through all points in the "timeseries"        
        #Calculate Tds, gv dqv, gl dql, and gi dqi between the current point and the next point in the "timeseries". 
        #These quantities will be used to calculate Qin        
        Tds=-0.5 * (t[i+1] + t[i]) * (s[i+1] - s[i])
        gvdqv=-0.5 * (gv[i+1] + gv[i]) * (qv[i+1] - qv[i])
        gldql=-0.5 * (gl[i+1] + gl[i]) * (ql[i+1] - ql[i])
        gidqi=-0.5 * (gi[i+1] + gi[i]) * (qfr[i+1] - qfr[i])
        #Calculate ds, gv/T dqv, gl/T dql, and gi/T dqi between the current point and the next point in the "timeseries".        
        ds=-(s[i+1] - s[i])
        gvdqv_T=-(gv[i+1] + gv[i]) * (qv[i+1] - qv[i])/(t[i+1]+t[i])
        gldql_T=-(gl[i+1] + gl[i]) * (ql[i+1] - ql[i])/(t[i+1]+t[i])
        gidqi_T=-(gi[i+1] + gi[i]) * (qfr[i+1] - qfr[i])/(t[i+1]+t[i])
        #If any of these values is nan, set them instead to zero, because if we add "nan" values to any sum, that sum becomes "nan". Setting them to zero ignores these values in the forthcoming sums     
        if np.isnan(Tds): 
            Tds=0
        if np.isnan(gvdqv):
            gvdqv=0
        if np.isnan(gldql):
            gldql=0
        if np.isnan(gidqi):
            gidqi=0
        if np.isnan(ds): 
            ds=0            
        if np.isnan(gvdqv_T):
            gvdqv_T=0
        if np.isnan(gldql_T):
            gldql_T=0
        if np.isnan(gidqi_T):
            gidqi_T=0              
        #Calculate the heating, dq, and heating normalized by temperature, dq/T. 
        #We define dq as in Pauluis and Zhang (2017, JAS) equation (7)        
        delq=Tds + gvdqv + gldql + gidqi #Heating calculated between the current and next point in the "timeseries"
        delq_T=ds+ gvdqv_T + gldql_T + gidqi_T #Heating normalized by temperature calculated between the current and next point in the "timeseries"      
        #Following Pauluis and Zhang (2017, JAS) equations (15) and (17), we only add dq and dq/T to the sums that will become Qout and Qout/Tout for 
        #this trajectory if dq<0 and dq/T<0, respectively. Note that dq<0 should imply dq/T<0 because T is positive-definite        
        if delq<0:
            delq_neg+=delq #Add to the sum that will become Qout for this trajectory
            if delq_T>0:
                print("ERROR!!!- even if dq<0, dq/T>0!!!")
        if delq_T<0: 
            delq_T_neg+=delq_T #Add to the sum that will become Qout/Tout for this trajectory
            if delq>0:
                print("ERROR!!!- even if dq>0, dq/T<0!!!")
    #The above code obtained dq and dq/T between all points in the "timeseries" except between the last point and first point (recall that the 
    #trajectories are closed loops by construction). Therefore, we must handle this case as well. The code below is as above but specifically considers
    #the first and last points in the "timeseries". Note that if the input "timeseries" are constructed such that the last point is the same as the first 
    #point, the code below will return zero values for "delq" and "delq_T", and so does not alter the values of "delq_neg" or "delq_T_neg". However, 
    #if instead the input "timeseries" has different last and first points, this code can account for that so that it is not a problem.
    Tds=-0.5 * (t[0] + t[-1]) * (s[0] - s[-1])
    gvdqv=-0.5 * (gv[0] + gv[-1]) * (qv[0] - qv[-1])
    gldql=-0.5 * (gl[0] + gl[-1]) * (ql[0] - ql[-1])
    gidqi=-0.5 * (gi[0] + gi[-1]) * (qfr[0] - qfr[-1])  
    ds=-(s[0] - s[-1])
    gvdqv_T=-(gv[0] + gv[-1]) * (qv[0] - qv[-1])/(t[0]+t[-1])
    gldql_T=-(gl[0] + gl[-1]) * (ql[0] - ql[-1])/(t[0]+t[-1])
    gidqi_T=-(gi[0] + gi[-1]) * (qfr[0] - qfr[-1])/(t[0]+t[-1])   
    if np.isnan(Tds): 
        Tds=0    
    if np.isnan(gvdqv):
        gvdqv=0
    if np.isnan(gldql):
        gldql=0
    if np.isnan(gidqi):
        gidqi=0   
    if np.isnan(ds): 
        ds=0    
    if np.isnan(gvdqv_T):
        gvdqv_T=0
    if np.isnan(gldql_T):
        gldql_T=0
    if np.isnan(gidqi_T):
        gidqi_T=0         
    delq=Tds + gvdqv + gldql + gidqi
    delq_T=ds+ gvdqv_T + gldql_T + gidqi_T
    if delq<0:
        delq_neg+=delq 
            #if delq_T>0: #OPTIONAL- uncomment this section if the input "timeseries" have their first point different from their last point. However, if the 
            #             #first point is equal to the last point then you should comment out this check since we expect dq, dq/T==0 in these cases.
            #             #Because of numerical errors in Python, in these cases dq and dq/T may not quite be equal to zero but may be small, and 
            #             #potentially opposite-signed. If this occurs then the error message below will be printed but would not reflect an actual problem. 
            #    print("ERROR!!!- even if dq<0, dq/T>0!!!")         
    if delq_T<0:
        delq_T_neg+=delq_T    
            #if delq>0: #OPTIONAL- uncomment this section if the input "timeseries" have their first point different from their last point. However, if the 
            #             #first point is equal to the last point then you should comment out this check since we expect dq, dq/T==0 in these cases.
            #             #Because of numerical errors in Python, in these cases dq and dq/T may not quite be equal to zero but may be small, and 
            #             #potentially opposite-signed. If this occurs then the error message below will be printed but would not reflect an actual problem. 
            #    print("ERROR!!!- even if dq>0, dq/T<0!!!")        
    return [delq_neg, delq_T_neg] #Return Qout and Qout/Tout for the current trajectory

The following code calculates the MAFALDA-derived energetic quantities Wmax, W, etc., given several input "timeseries" derived from a given MAFALDA trajectory from the isentropic streamfunction.

The inputs are:
1. Temperature (K) "timeseries"
2. Moist entropy (J/kg/K) "timeseries" 
3. Specific volume (m^3/kg) "timeseries"
4. Pressure (Pa) "timeseries"
5. WP_integrand "timeseries"
6. Height (m) "timeseries"
7. Three Gibbs free energy (J/kg) "timeseries" for the Gibbs free energy of water vapor, liquid water, and solid water
8. Three mixing ratio (kg/kg) "timeseries" for the mixing ratios of water vapor, liquid water, and solid water

The ouputs are:
1. The maximum available energy for the trajectory, $W_{Max}$
2. The total useful energy produced by the trajectory, $W=W_{P}+W_{KE}$
3. The water-lifting energy, $W_{P}$
4. The three contributions to the Gibbs penalty $\Delta G$ from water vapor, liquid water, and solid water

In [ ]:
def MAFALDA(t, s, ad, p, WPint, z, gv, qv, gl, ql, gi, qfr): 
    end=len(s) #Length of the "timeseries" for this MAFALDA trajectory
    #Initialize output variables
    Tds=0
    addp=0
    dWp=0
    gvdqv=0
    gldql=0
    gidqi=0
    for i in range(end-1): #Loop through all points in the "timeseries" 
        #Calculate Tds, -alpha_d dp, etc. between the current point and the next point in the "timeseries". 
        #These quantities will be used to calculate the MAFALDA-derived energetic variables      
        #Note that W=-closed_loop_integral(alpha_d dp), whereas this negative sign does not exist for other terms such 
        #as Wmax = closed_loop_integral(Tds). This difference in sign for alpha_d dp is accounted for in the code below
        Tds_c=-0.5 * (t[i+1] + t[i]) * (s[i+1] - s[i])
        addp_c=0.5 * (ad[i+1] + ad[i]) * (p[i+1] - p[i])  
        dWp_c=-0.5 * (WPint[i+1] + WPint[i]) * (z[i+1] - z[i])
        gvdqv_c=-0.5 * (gv[i+1] + gv[i]) * (qv[i+1] - qv[i])
        gldql_c=-0.5 * (gl[i+1] + gl[i]) * (ql[i+1] - ql[i])
        gidqi_c=-0.5 * (gi[i+1] + gi[i]) * (qfr[i+1] - qfr[i])       
        #If any of these values is nan, set them instead to zero, because if we add "nan" values to any sum, that sum becomes "nan". Setting them to zero ignores these values in the forthcoming sums 
        if np.isnan(Tds_c): 
            Tds_c=0
        if np.isnan(addp_c):
            addp_c=0
        if np.isnan(dWp_c):
            dWp_c=0            
        if np.isnan(gvdqv_c):
            gvdqv_c=0
        if np.isnan(gldql_c):
            gldql_c=0
        if np.isnan(gidqi_c):
            gidqi_c=0
        #Add these quantities to the sums that will become the MAFALDA-derived energetic variables Wmax, W, etc. for this trajectory
        Tds+=Tds_c
        dWp+=dWp_c
        addp+=addp_c
        gvdqv+=gvdqv_c
        gldql+=gldql_c
        gidqi+=gidqi_c
    #The above code obtained "Tds_c", etc. between all points in the "timeseries" except between the last point and first point (recall that the 
    #trajectories are closed loops by construction). Therefore, we must handle this case as well. The code below is as above but specifically considers
    #the first and last points in the "timeseries". Note that if the input "timeseries" are constructed such that the last point is the same as the first 
    #point, the code below will return zero values for "Tds_c", etc., and so does not alter the values of "Tds", etc.. However, 
    #if instead the input "timeseries" has different last and first points, this code can account for that so that it is not a problem.
    Tds_c=-0.5 * (t[0] + t[-1]) * (s[0] - s[-1])
    addp_c=0.5 * (ad[0] + ad[-1]) * (p[0] - p[-1])
    dWp_c=-0.5 * (WPint[0] + WPint[-1]) * (z[0] - z[-1])
    gvdqv_c=-0.5 * (gv[0] + gv[-1]) * (qv[0] - qv[-1])
    gldql_c=-0.5 * (gl[0] + gl[-1]) * (ql[0] - ql[-1])
    gidqi_c=-0.5 * (gi[0] + gi[-1]) * (qfr[0] - qfr[-1])  
    if np.isnan(Tds_c): 
        Tds_c=0
    if np.isnan(addp_c):
        addp_c=0
    if np.isnan(dWp_c):
        dWp_c=0            
    if np.isnan(gvdqv_c):
        gvdqv_c=0
    if np.isnan(gldql_c):
        gldql_c=0
    if np.isnan(gidqi_c):
        gidqi_c=0  
    Tds+=Tds_c
    addp+=addp_c
    dWp+=dWp_c
    gvdqv+=gvdqv_c
    gldql+=gldql_c
    gidqi+=gidqi_c
    return [Tds, addp, dWp, gvdqv, gldql, gidqi] #Return Wmax, W, Wp, and the contributions from water vapor, liquid
                                                 #water, and solid water to the Gibbs penalty for the current trajectory

The following code removes all "nan" values from an input "timeseries" derived from a specific MAFALDA trajectory of the isentropic streamfunction. The code removes these values via an averaging process, illustrated in the example below:

Input "timeseries": [1, 2, 3, nan, nan, 4]

Iteration 1- remove first nan value by averaging closest non-nan values: [1, 2, 3, 3.5, nan, 4]

Iteration 2- remove second nan value by averaging closest non-nan values: [1, 2, 3, 3.5, 3.75, 4]

This nan-replacement methodology was verified to perform well by visual inspection of the MAFALDA trajectories in various spaces, such as T-s space, before and after this routine was applied to them.

The input is:
1. The input "timeseries" 

The output is:
1. The same "timeseries" with "nan" values removed as described above.

In [ ]:
def average_nans_cnum(interpolated_var):
    var_re_inds=[] #Contains indices corresponding to non-nan values
    #Save indices where non-nan values occur in the "timeseries"
    for i in np.arange(0, size(interpolated_var)): 
        if not np.isnan(interpolated_var[i]):
            var_re_inds.append(i)
    if len(var_re_inds)==len(interpolated_var): #If no nan entries exist in the input "timeseries"
        return(interpolated_var) #Return the input "timeseries", unchanged
    elif len(var_re_inds)<len(interpolated_var): #If nan values exist in the "timeseries"
        si=var_re_inds[0] #Index of the first non-nan value in the "timeseries"
        li=var_re_inds[-1] #Index of the last non-nan value in the "timeseries"
        if (si>0) or li<len(interpolated_var)-1: #This is the case where nan values exist at the start and/or end of the "timeseries" (and 
                                                 #possibly also at other points in the timeseries), as in these example vectors:
                                                 #[nan, 1, 2, 3, 4]; [1, 2, 3, 4, nan]; [nan, 1, 2, 3, nan]; [nan, 1, 2, nan, 4].
            if len(var_re_inds)==len(interpolated_var)-1: #Case where only one nan entry exists. Given the earlier condition, this must then be an entry at one or both of the first and last entries of the "timeseries"
                if si==1: #If the nan entry is the first one in the "timeseries"
                    interpolated_var[0]=np.mean([interpolated_var[si], interpolated_var[li]])
                    return(interpolated_var) #Return the timeseries" with nan values now removed
                else: #If the nan entry is the last one in the "timeseries"
                    interpolated_var[li+1]=np.mean([interpolated_var[si], interpolated_var[li]]) 
                    return(interpolated_var) #Return the timeseries" with nan values now removed
            else: #Case where there is more than one nan entry, so we cannot guarantee that all nan values occur at the first and last entries of the "timeseries"
                #Deal first with the nan values around the "edges" of the "timeseries"
                for i in np.arange(li+1, len(interpolated_var)): #Get rid of all nan values between the last non-nan value and the end of the "timeseries"
                    interpolated_var[i]=np.mean([interpolated_var[i-1], interpolated_var[si]])
                for i in np.arange(0, si): #Get rid of all nan values between the first entry and the first non-nan entry in the "timeseries"
                    if i==0: #Deal with the special case of the first entry
                        interpolated_var[i]=np.mean([interpolated_var[len(interpolated_var)-1], interpolated_var[si]])
                    else: #Deal with all other nan entries before the first non-nan value
                        interpolated_var[i]=np.mean([interpolated_var[i-1], interpolated_var[si]])
                #Now, we apply our methodology to nan values that are not at the "edges" of the timeseries, as in the nan values in these example vectors:
                #[1, 2, nan, 4, 5]; [1, nan, 3, 4, 5]
                if sum(np.isnan(interpolated_var))==0: #Case where no such nan values exist  
                    return(interpolated_var) #Return the "timeseries" with all nan values now removed
                else: #Case where such nan values exist
                    for i in np.arange(0, len(var_re_inds)-1): #Loop through the set of non-nan values we obtained at the beginning of this procedure
                        rei=var_re_inds[i] #Index of current non-nan value
                        rei2=var_re_inds[i+1] #Index of next non-nan value
                        #Apply the nan-removal averaging procedure to all nan values between the non-nan values denoted by the indices rei and rei2
                        for i in np.arange(rei+1, rei2):
                            interpolated_var[i]=np.mean([interpolated_var[i-1], interpolated_var[rei2]])           
                    return(interpolated_var) #Return the "timeseries" with nan values now removed
        else: #Deals with the case where nans are not at the "edges" of the array but occur at other points, as in the previous set of example vectors
            for i in np.arange(0, len(var_re_inds)-1):
                rei=var_re_inds[i]
                rei2=var_re_inds[i+1]
                for i in np.arange(rei+1, rei2):
                    interpolated_var[i]=np.mean([interpolated_var[i-1], interpolated_var[rei2]])           
            return(interpolated_var) #Return the "timeseries" with nan values now removed       

The following code is for formatting of plot labels only. It converts labels to scientific notation. Source: https://python.tutorialink.com/scientific-notation-colorbar-in-matplotlib/

In [ ]:
def fmt(x, pos): 
    a, b = '{:.2e}'.format(x).split('e')
    b = int(b)
    return r'${} \times 10^{{{}}}$'.format(a, b)

## Perform MAFALDA for "single-eyewall" periods

The code below applies the MAFALDA procedure to the "single-eyewall" periods for all SSTs. 

In [ ]:
SSTs=np.arange(295, 308, 0.5) #SSTs range from 295K to 307.5K in steps of 0.5K for our simulations.
L_out=600 #Outer radius (km) for the MAFALDA analysis. This value is subjectively set based on the single-eyewall period data.
cval=0.82 #Eyewall circulation threshold (dimensionless). Minimum fraction of (SST-T_tropopause) temperature difference 
        #represented by "eyewall trajectories". This threshold is subjectively set based on the single-eyewall period data.
for i in np.arange(len(SSTs)): #Loop through all SST values
    SST_c=SSTs[i] #Set current SST value
    if SST_c-floor(SST_c)==0: #We need any SST that is an integer value to be loaded as such, rather than a floating-point value.
                              #e.g., we want SST_c=295 and not SST_c=295.0. However, the SST as loaded will be a floating-point
                              #number. The code below converts it to an integer.
        SST_c=int(SST_c) 
    print("SST is "+np.str(SST_c))
    tstart=np.load('Time_bounds_'+np.str(SST_c)+'_RMW_Rp.npz')['time_bounds_Rp'][0] #Timestep corresponding to the start of the 
                                                                                    #single-eyewall time period for this SST
    tfinal=np.load('Time_bounds_'+np.str(SST_c)+'_RMW_Rp.npz')['time_bounds_Rp'][1] #Timestep immediately after the end of the 
                                                                                    #single-eyewall time period for this SST
    MAFALDA_process_singleeyewall(SST_c, tstart, tfinal, L_out, cval) #Perform the MAFALDA procedure on the data from the selected
                                                                    #single-eyewall period.

## Make supplemetary figure plots

The following code makes some of the supplementary figure plots for the paper given outputs saved by this code and by MAFALDA_manywindows.py (when these are run with the correct input values of L_out, cval, and SST)

In [ ]:
#Figure S4: Plot single-eyewall Eulerian streamfunctions at 295K, 295.5K, 307K, and 307.5K
SSTs=np.asarray([int(295), 295.5, int(307), 307.5]) #Set SST values
plt.rc('xtick', labelsize=15)    # fontsize of the x tick labels
plt.rc('ytick', labelsize=15)    # fontsize of the y tick labels
fig, ax=plt.subplots(2, 2, figsize=(15, 10)) #Create a 2 x 2 set of subplots.
#i and j control the position of each of the four plots plot in plt.subplots
i=0 
j=0
for SST_c in SSTs:
    if SST_c-floor(SST_c)==0:
        SST_c=int(SST_c) #If the SST is an integer, convert from floating-point number to an integer.
    #Load saved data from the code above. The user will need to additionally run the MAFALDA process with L_out=1200 for SST=295, 295.5, 307, and 307.5 to make these plots
    r=np.load("SM_streamf_"+np.str(SST_c)+".npz")["r"]
    z=np.load("SM_streamf_"+np.str(SST_c)+".npz")["z"]
    streamf=np.load("SM_streamf_"+np.str(SST_c)+".npz")["streamf"]
    ncontour=np.load("SM_streamf_"+np.str(SST_c)+".npz")["ncontour"]
    #Plot Eulerian streamfunction for the current SST
    [rplot, zplot]=np.meshgrid(r, z)
    conts=ax[j, i].contour(rplot/1000, zplot/1000, streamf, int(ncontour), cmap='viridis')
    ax[j, i].set_ylabel('Height (km)', fontsize=20)
    ax[j, i].set_xlabel('Radial distance (km)', fontsize=20)
    ax[j, i].set_title("Eulerian streamfunction (kg s$^{-1}$)", fontsize=20)
    cb=plt.colorbar(conts, ax=ax[j, i]) #Add colorbar
    cb.formatter.set_powerlimits((0, 0)) #Format colorbar
    cb.formatter.set_useMathText(True)
    cb.ax.yaxis.set_offset_position('left')
    i+=1
    if i==2:
        i=0
        j=1
#Share x axis between subplots
ax[1, 0].sharex(ax[0, 0]) 
ax[1, 1].sharex(ax[0, 1])   

plt.tight_layout() #Adjust the spacing between figures so that axis and colorbar labels don't overlap

plt.savefig("SFigure_Lotests.png") #Save figure S4

#Figure S5: Plot different isentropic streamfunctions for different c values: 295K, 296.5K, and 298.5K for c=0.82; 
#and 300.5K for c=0.85
SSTs=np.asarray([int(295), 296.5, 298.5, 302.5]) #Create a 2 x 2 set of subplots. 
plt.rc('xtick', labelsize=15)    # fontsize of the x tick labels
plt.rc('ytick', labelsize=15)    # fontsize of the y tick labels
fig, ax=plt.subplots(2, 2, figsize=(15, 10))
#i and j control the position of each of the four plots plot in plt.subplots
i=0
j=0
for SST_c in SSTs:
    if SST_c-floor(SST_c)==0:
        SST_c=int(SST_c) #If the SST is an integer, convert from floating-point number to an integer.
    #Load saved data from the code above. The user will need to additionally run the MAFALDA process with c=0.85 for SST=300.5 to make these plots
    th_min=np.load("SM_ctests_1_"+np.str(SST_c)+".npz")["th_min"]
    th_max=np.load("SM_ctests_1_"+np.str(SST_c)+".npz")["th_max"]
    delt=np.load("SM_ctests_1_"+np.str(SST_c)+".npz")["delt"]
    interpolant_th_arr=np.load("SM_ctests_1_"+np.str(SST_c)+".npz", allow_pickle=True)["interpolant_th_arr"]
    interpolant_z_arr=np.load("SM_ctests_1_"+np.str(SST_c)+".npz", allow_pickle=True)["interpolant_z_arr"]
    psi=np.load("SM_ctests_1_"+np.str(SST_c)+".npz", allow_pickle=True)["psi"]
    rainband_cnums=np.load("SM_ctests_1_"+np.str(SST_c)+".npz")["rainband_cnums"]
    overturning_cnums=np.load("SM_ctests_1_"+np.str(SST_c)+".npz")["overturning_cnums"]
    #Plot isentropic streamfunction for the current set of data. Plot eyewall trajectories in red and rainband trajectories in blue
    theta_es=np.arange(th_min, th_max, delt*2)
    [zplot, thplot]=np.meshgrid(theta_es, z) 
    ncontour = 25
    contourarray = psi.min()*((2*np.arange((ncontour+1),1.0, -1.0)-1)/(2*ncontour))
    for cnum in rainband_cnums: #Plot each rainband trajectory
        ax[j, i].plot(interpolant_th_arr[cnum],interpolant_z_arr[cnum]/1000, color='blue')#, label = 'Contour number = %s' %cnum)
        ax[j, i].set_xlabel('Equivalent Potential Temperature (K)')
        ax[j, i].set_ylabel('Height (km)')
        ax[j, i].set_title('Isentropic Streamfunction', fontsize=25)
    for cnum in overturning_cnums: #Plot each eyewall trajectory
        ax[j, i].plot(interpolant_th_arr[cnum],interpolant_z_arr[cnum]/1000, color='red')#, label = 'Contour number = %s' %cnum)
        ax[j, i].set_xlabel('Equivalent Potential Temperature (K)')
        ax[j, i].set_ylabel('Height (km)')
        ax[j, i].set_title('Isentropic Streamfunction', fontsize=25)    
    ax[j, i].set_ylabel('Height (km)')
    ax[j, i].set_xlabel('Equivalent Potential Temperature (K)')
    ax[j, i].set_xlim(300, 370)
    ax[j, i].set_ylim(-0.5, 14)       
    i+=1
    if i==2:
        i=0
        j=1
#Share x axis between subplots
ax[1, 0].sharex(ax[0, 0])
ax[1, 1].sharex(ax[0, 1]) 

plt.tight_layout() #Adjust the spacing between figures so that axis and colorbar labels don't overlap

plt.savefig("SFigure_ctests.png") #Save figure S5